https://huggingface.co/deepset/roberta-base-squad2










https://docs.haystack.deepset.ai/docs/migration#migration-examples

In [1]:
!pip install haystack-ai

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 515.1/515.1 kB 10.9 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 100.0/100.0 kB 7.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 74.5/74.5 kB 5.3 MB/s eta 0:00:00


In [4]:
!pip install haystack-ai

In [ ]:
# Clone the repo
git clone https://github.com/deepset-ai/haystack.git

# Move into the cloned folder
cd haystack

# Upgrade pip
pip install --upgrade pip

# Install Haystack in editable mode
pip install -e '.[dev]'

In [1]:
from haystack.components.document_stores import InMemoryDocumentStore
from haystack.pipelines import ExtractiveQAPipeline
from haystack import Document
from haystack.components.retrievers import BM25Retriever
from haystack.nodes import FARMReader

document_store = InMemoryDocumentStore(use_bm25=True)
document_store.write_documents([
    Document(content="Paris is the capital of France."),
    Document(content="Berlin is the capital of Germany."),
    Document(content="Rome is the capital of Italy."),
    Document(content="Madrid is the capital of Spain."),
])

retriever = BM25Retriever(document_store=document_store)
reader = FARMReader(model_name_or_path="deepset/roberta-base-squad2")
extractive_qa_pipeline = ExtractiveQAPipeline(reader, retriever)

query = "What is the capital of France?"
result = extractive_qa_pipeline.run(
        query=query,
        params={
                "Retriever": {"top_k": 10},
                "Reader": {"top_k": 5}
        }
)

ModuleNotFoundError: No module named 'haystack.components.document_stores'

In [3]:
from haystack.document_stores.in_memory import InMemoryDocumentStore
from haystack import Document, Pipeline
from haystack.components.retrievers.in_memory import InMemoryBM25Retriever
from haystack.components.readers import ExtractiveReader

document_store = InMemoryDocumentStore()
document_store.write_documents([
    Document(content="Paris is the capital of France."),
    Document(content="Berlin is the capital of Germany."),
    Document(content="Rome is the capital of Italy."),
    Document(content="Madrid is the capital of Spain."),
])

retriever = InMemoryBM25Retriever(document_store)
reader = ExtractiveReader(model="deepset/roberta-base-squad2")
extractive_qa_pipeline = Pipeline()
extractive_qa_pipeline.add_component("retriever", retriever)
extractive_qa_pipeline.add_component("reader", reader)
extractive_qa_pipeline.connect("retriever", "reader")

query = "What is the capital of France?"
result = extractive_qa_pipeline.run(data={
        "retriever": {"query": query, "top_k": 3},
        "reader": {"query": query, "top_k": 2}
})

display(result)

{'reader': {'answers': [ExtractedAnswer(query='What is the capital of France?', score=0.5835986733436584, data='Paris', document=Document(id=0f5beda04153dbfc462c8b31f8536749e43654709ecf0cfe22c6d009c9912214, content: 'Paris is the capital of France.', score: 1.9188925512689656), context=None, document_offset=ExtractedAnswer.Span(start=0, end=5), context_offset=None, meta={}),
   ExtractedAnswer(query='What is the capital of France?', score=0.3539331257343292, data='Berlin', document=Document(id=312b465e77e25c11512ee76ae699ce2eb201f34c8c51384003bb367e24fb6cf8, content: 'Berlin is the capital of Germany.', score: 1.25001877108789), context=None, document_offset=ExtractedAnswer.Span(start=0, end=6), context_offset=None, meta={}),
   ExtractedAnswer(query='What is the capital of France?', score=0.2690231035529411, data=None, document=None, context=None, document_offset=None, context_offset=None, meta={})]}}

In [5]:
# Create a dummy text file for demonstration
with open("input.txt", "w") as f:
    f.write("Paris is the capital of France.\n")
    f.write("Berlin is the capital of Germany.\n")
    f.write("Rome is the capital of Italy.\n")
    f.write("Madrid is the capital of Spain.\n")

In [ ]:
/content/input.txt

In [8]:
from haystack.document_stores.in_memory import InMemoryDocumentStore
from haystack import Document, Pipeline
from haystack.components.retrievers.in_memory import InMemoryBM25Retriever
from haystack.components.readers import ExtractiveReader

# Read content from the text file
with open("input.txt", "r") as f:
    file_content = f.read()

document_store = InMemoryDocumentStore()
# Write the content of the file as a single document
document_store.write_documents([Document(content=file_content)])

retriever = InMemoryBM25Retriever(document_store)
reader = ExtractiveReader(model="deepset/roberta-base-squad2")
extractive_qa_pipeline = Pipeline()
extractive_qa_pipeline.add_component("retriever", retriever)
extractive_qa_pipeline.add_component("reader", reader)
extractive_qa_pipeline.connect("retriever", "reader")

query = "What is the capital of France?"
result = extractive_qa_pipeline.run(data={
        "retriever": {"query": query, "top_k": 1},
        "reader": {"query": query, "top_k": 1}
})

display(result)

{'reader': {'answers': [ExtractedAnswer(query='What is the capital of France?', score=0.5785729289054871, data='Paris', document=Document(id=d283a2c2582cfebb26c86dbac6ac4d798ac92d4bb128ca692ab382ee342e49e3, content: 'Paris is the capital of France.
   
   ', score: 1.4983441273530254), context=None, document_offset=ExtractedAnswer.Span(start=0, end=5), context_offset=None, meta={}),
   ExtractedAnswer(query='What is the capital of France?', score=0.42142707109451294, data=None, document=None, context=None, document_offset=None, context_offset=None, meta={})]}}

In [10]:
from haystack.document_stores.in_memory import InMemoryDocumentStore
from haystack import Document, Pipeline
from haystack.components.retrievers.in_memory import InMemoryBM25Retriever
from haystack.components.readers import ExtractiveReader

document_store = InMemoryDocumentStore()
documents = []

# Read content from the text file line by line and create a document for each line
with open("input_long.txt", "r") as f:
    for line in f:
        # Create a Document object for each non-empty line
        if line.strip():
            documents.append(Document(content=line.strip()))

# Write all documents to the document store
document_store.write_documents(documents)

retriever = InMemoryBM25Retriever(document_store)
reader = ExtractiveReader(model="deepset/roberta-base-squad2")
extractive_qa_pipeline = Pipeline()
extractive_qa_pipeline.add_component("retriever", retriever)
extractive_qa_pipeline.add_component("reader", reader)
extractive_qa_pipeline.connect("retriever", "reader")

query = "What is the capital of France?"
result = extractive_qa_pipeline.run(data={
        "retriever": {"query": query, "top_k": 3}, # Retrieve top 3 relevant documents
        "reader": {"query": query, "top_k": 1} # Extract top 1 answer from retrieved documents
})

display(result)

{'reader': {'answers': [ExtractedAnswer(query='What is the capital of France?', score=0.5835986733436584, data='Paris', document=Document(id=0f5beda04153dbfc462c8b31f8536749e43654709ecf0cfe22c6d009c9912214, content: 'Paris is the capital of France.', score: 4.153645303111382), context=None, document_offset=ExtractedAnswer.Span(start=0, end=5), context_offset=None, meta={}),
   ExtractedAnswer(query='What is the capital of France?', score=0.41640132665634155, data=None, document=None, context=None, document_offset=None, context_offset=None, meta={})]}}

In [11]:
# Create a dummy text file with more content for demonstration
with open("input_long.txt", "w") as f:
    f.write("Paris is the capital of France.\n")
    f.write("The Eiffel Tower is a famous landmark in Paris.\n")
    f.write("Berlin is the capital of Germany.\n")
    f.write("The Brandenburg Gate is in Berlin.\n")
    f.write("Rome is the capital of Italy.\n")
    f.write("The Colosseum is an ancient amphitheater in Rome.\n")
    f.write("Madrid is the capital of Spain.\n")
    f.write("The Royal Palace of Madrid is the official residence of the Spanish royal family.\n")
    f.write("London is the capital of the United Kingdom.\n")
    f.write("Buckingham Palace is the administrative headquarters of the monarch of the United Kingdom.\n")

In [14]:
from haystack.document_stores.in_memory import InMemoryDocumentStore
from haystack import Document, Pipeline
from haystack.components.retrievers.in_memory import InMemoryBM25Retriever
from haystack.components.readers import ExtractiveReader
from haystack.components.preprocessors import DocumentSplitter

document_store = InMemoryDocumentStore()
documents = []

# Read content from the text file
with open("input_large.txt", "r") as f:
    file_content = f.read()

# Initialize the DocumentSplitter
# You can adjust parameters like unit, length, and overlap based on your needs
splitter = DocumentSplitter(split_by="word", split_length=100, split_overlap=20)

# Split the file content into smaller documents
split_documents = splitter.run(documents=[Document(content=file_content)])['documents']

# Write the split documents to the document store
document_store.write_documents(split_documents)

retriever = InMemoryBM25Retriever(document_store)
reader = ExtractiveReader(model="deepset/roberta-base-squad2")
extractive_qa_pipeline = Pipeline()

# Add components to the pipeline
extractive_qa_pipeline.add_component("retriever", retriever)
extractive_qa_pipeline.add_component("reader", reader)

# Connect the components
extractive_qa_pipeline.connect("retriever", "reader")

query = "What is the capital of France?" # You might want to change the query to match the new document content
result = extractive_qa_pipeline.run(data={
        "retriever": {"query": query, "top_k": 3}, # Retrieve top 3 relevant documents
        "reader": {"query": query, "top_k": 1} # Extract top 1 answer from retrieved documents
})

display(result)

{'reader': {'answers': [ExtractedAnswer(query='What is the capital of France?', score=0.6209893226623535, data=None, document=None, context=None, document_offset=None, context_offset=None, meta={}),
   ExtractedAnswer(query='What is the capital of France?', score=0.3790106773376465, data='Revelation\n', document=Document(id=83252374a3f0f06473f041890e186eb749ccb00489444575bba1dc5f562fa75d, content: 'staff.
   Her path led her through treacherous mountains and dense forests, facing many trials along th...', meta: {'source_id': 'd2770620d6c280ccf08cfb81cd94ad56456944aa78d4cb4580fc1ba201898d07', 'page_number': 1, 'split_id': 1, 'split_idx_start': 474, '_split_overlap': [{'doc_id': '9ce54b617964aa0a4b89b2859130d565f7292364829825db2b7885351ad05c67', 'range': (474, 620)}]}, score: 0.3665896070768126), context=None, document_offset=ExtractedAnswer.Span(start=205, end=216), context_offset=None, meta={'answer_page_number': 1})]}}

In [16]:
from haystack.document_stores.in_memory import InMemoryDocumentStore
from haystack import Document, Pipeline
from haystack.components.retrievers.in_memory import InMemoryBM25Retriever
from haystack.components.readers import ExtractiveReader

document_store = InMemoryDocumentStore()
documents = []

# Read content from the text file line by line and create a document for each line
with open("input_long.txt", "r") as f:
    for line in f:
        # Create a Document object for each non-empty line
        if line.strip():
            documents.append(Document(content=line.strip()))

# Write all documents to the document store
document_store.write_documents(documents)

retriever = InMemoryBM25Retriever(document_store)
reader = ExtractiveReader(model="deepset/roberta-base-squad2")
extractive_qa_pipeline = Pipeline()
extractive_qa_pipeline.add_component("retriever", retriever)
extractive_qa_pipeline.add_component("reader", reader)
extractive_qa_pipeline.connect("retriever", "reader")

query = "What is the capital of France?"
result = extractive_qa_pipeline.run(data={
        "retriever": {"query": query, "top_k": 3}, # Retrieve top 3 relevant documents
        "reader": {"query": query, "top_k": 1} # Extract top 1 answer from retrieved documents
})

display(result)

{'reader': {'answers': [ExtractedAnswer(query='What is the capital of France?', score=0.5835986733436584, data='Paris', document=Document(id=0f5beda04153dbfc462c8b31f8536749e43654709ecf0cfe22c6d009c9912214, content: 'Paris is the capital of France.', score: 4.153645303111382), context=None, document_offset=ExtractedAnswer.Span(start=0, end=5), context_offset=None, meta={}),
   ExtractedAnswer(query='What is the capital of France?', score=0.41640132665634155, data=None, document=None, context=None, document_offset=None, context_offset=None, meta={})]}}

In [15]:
# Create a dummy text file with more content for demonstration
with open("input_large.txt", "w") as f:
    f.write("Chapter 1: The Beginning\n\n")
    f.write("It was a dark and stormy night. The wind howled through the trees, and the rain beat against the windowpanes.\n")
    f.write("In a small cottage nestled deep within the woods, a young woman named Elara sat by the fire, reading an ancient tome.\n")
    f.write("She was searching for a forgotten spell, one that could break the curse that plagued her village.\n\n")
    f.write("Chapter 2: The Journey\n\n")
    f.write("The next morning, Elara set out on her journey. She packed a few provisions and her most trusted staff.\n")
    f.write("Her path led her through treacherous mountains and dense forests, facing many trials along the way.\n")
    f.write("She encountered mythical creatures and solved riddles posed by ancient guardians.\n\n")
    f.write("Chapter 3: The Revelation\n\n")
    f.write("After many weeks, Elara finally reached the hidden temple. Inside, she found the spell she was looking for.\n")
    f.write("But the spell required a sacrifice, one that Elara was willing to make to save her people.\n")
    f.write("With a heavy heart, she performed the ritual, and a bright light filled the temple.\n")

In [ ]:
from haystack.document_stores.in_memory import InMemoryDocumentStore
from haystack import Document, Pipeline
from haystack.components.retrievers.in_memory import InMemoryBM25Retriever
from haystack.components.readers import ExtractiveReader

document_store = InMemoryDocumentStore()
documents = []

# Read content from the text file line by line and create a document for each line
with open("input_long.txt", "r") as f:
    for line in f:
        # Create a Document object for each non-empty line
        if line.strip():
            documents.append(Document(content=line.strip()))

# Write all documents to the document store
document_store.write_documents(documents)

retriever = InMemoryBM25Retriever(document_store)
reader = ExtractiveReader(model="deepset/roberta-base-squad2")
extractive_qa_pipeline = Pipeline()
extractive_qa_pipeline.add_component("retriever", retriever)
extractive_qa_pipeline.add_component("reader", reader)
extractive_qa_pipeline.connect("retriever", "reader")

query = "What is the capital of France?"
result = extractive_qa_pipeline.run(data={
        "retriever": {"query": query, "top_k": 3}, # Retrieve top 3 relevant documents
        "reader": {"query": query, "top_k": 1} # Extract top 1 answer from retrieved documents
})

display(result)

In [17]:
!pip install farm-haystack[all]


     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 154.1/154.1 kB 7.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 64.6/64.6 kB 4.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 42.8/42.8 kB 3.5 MB/s eta 0:00:00
  Installing build dependencies ... done
  Getting requirements to build wheel ... done
  Preparing metadata (pyproject.toml) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 981.5/981.5 kB 24.9 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 800.5/800.5 kB 40.3 MB/s eta 0:00:00
  Installing build dependencies ... done
  Getting requirements to build wheel ... done
  Preparing metadata (pyproject.toml) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 43.6/43.6 kB 3.4 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 42.9/42.9 kB 3.4 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 50.1/50.1 kB 3.8 MB/s eta 0:00:00
INFO:

In [18]:
from haystack import Pipeline
from haystack.components.readers import ExtractiveReader
from haystack.components.retrievers.in_memory import InMemoryEmbeddingRetriever
from haystack.document_stores.in_memory import InMemoryDocumentStore
from haystack import Document

from sentence_transformers import SentenceTransformer
import nltk

# تحميل كتاب من ملف نصي
with open("book.txt", "r", encoding="utf-8") as f:
    full_text = f.read()

# تقسيم الكتاب إلى فقرات باستخدام NLTK
nltk.download('punkt')
paragraphs = nltk.tokenize.sent_tokenize(full_text)
chunks = [Document(content=para.strip()) for para in paragraphs if len(para.strip()) > 30]

# إعداد document store
document_store = InMemoryDocumentStore()
document_store.write_documents(chunks)

# تحميل نموذج embeddings (semantic)
embedding_model = SentenceTransformer("sentence-transformers/all-MiniLM-L6-v2")

# إعداد retriever باستخدام البحث الدلالي
retriever = InMemoryEmbeddingRetriever(embedding_model=embedding_model)
retriever.warm_up(document_store)  # بناء الفهرس الداخلي للمتجهات

# إعداد reader (لتوليد إجابات استخراجية)
reader = ExtractiveReader(model="deepset/roberta-base-squad2")

# إعداد pipeline
semantic_qa_pipeline = Pipeline()
semantic_qa_pipeline.add_component("retriever", retriever)
semantic_qa_pipeline.add_component("reader", reader)
semantic_qa_pipeline.connect("retriever", "reader")

# تنفيذ الاستعلام
query = "What are the effects of climate change?"
result = semantic_qa_pipeline.run(data={
    "retriever": {"query": query, "top_k": 5},
    "reader": {"query": query, "top_k": 2}
})

# عرض النتائج
for answer in result["reader"]["answers"]:
    print(f"- إجابة: {answer['answer']} (الثقة: {answer['score']:.2f})")


[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Unzipping tokenizers/punkt.zip.


LookupError: 
**********************************************************************
  Resource [93mpunkt_tab[0m not found.
  Please use the NLTK Downloader to obtain the resource:

  [31m>>> import nltk
  >>> nltk.download('punkt_tab')
  [0m
  For more information see: https://www.nltk.org/data.html

  Attempted to load [93mtokenizers/punkt_tab/english/[0m

  Searched in:
    - '/root/nltk_data'
    - '/usr/nltk_data'
    - '/usr/share/nltk_data'
    - '/usr/lib/nltk_data'
    - '/usr/share/nltk_data'
    - '/usr/local/share/nltk_data'
    - '/usr/lib/nltk_data'
    - '/usr/local/lib/nltk_data'
**********************************************************************


In [32]:
from haystack import Pipeline
from haystack.components.readers import ExtractiveReader
from haystack.components.retrievers.in_memory import InMemoryEmbeddingRetriever
from haystack.document_stores.in_memory import InMemoryDocumentStore
from haystack import Document
from haystack.components.embedders import SentenceTransformersTextEmbedder, SentenceTransformersDocumentEmbedder


from sentence_transformers import SentenceTransformer
import nltk
import re

# تحميل كتاب من ملف نصي
# Make sure you have a 'book.txt' file in your environment
try:
    with open("book.txt", "r", encoding="utf-8") as f:
        full_text = f.read()
except FileNotFoundError:
    print("Error: book.txt not found. Please upload the book file.")
    full_text = "" # Set empty text to avoid further errors if file not found

# تقسيم الكتاب إلى فقرات باستخدام NLTK أو طريقة أخرى
if full_text:
    try:
        nltk.download('punkt')
        paragraphs = nltk.tokenize.sent_tokenize(full_text)
        chunks = [Document(content=para.strip()) for para in paragraphs if len(para.strip()) > 30]
    except LookupError:
        print("NLTK punkt resource not found. Using regex for splitting.")
        # Fallback to regex splitting if NLTK resource is missing
        sentences = re.split(r'(?<=[.!?])\s+', full_text)
        chunks = [Document(content=sentence.strip()) for sentence in sentences if len(sentence.strip()) > 30]

    if not chunks:
        print("No chunks created from the document. Please check the file content or splitting logic.")
else:
    chunks = []

# إعداد document store
document_store = InMemoryDocumentStore()

# إعداد embedder لإنشاء تضمينات المستندات
document_embedder = SentenceTransformersDocumentEmbedder(model="sentence-transformers/all-MiniLM-L6-v2")
document_embedder.warm_up() # Warm up the document embedder

if chunks:
    # Generate embeddings for the documents
    embedded_documents = document_embedder.run(documents=chunks)["documents"]
    # Write the documents with embeddings to the document store
    document_store.write_documents(embedded_documents)


# إعداد embedder لإنشاء تضمينات الاستعلام
text_embedder = SentenceTransformersTextEmbedder(model="sentence-transformers/all-MiniLM-L6-v2")
text_embedder.warm_up() # Warm up the text embedder

# إعداد retriever باستخدام البحث الدلالي
retriever = InMemoryEmbeddingRetriever(document_store) # Pass the document store as a positional argument


# إعداد reader (لتوليد إجابات استخراجية)
reader = ExtractiveReader(model="deepset/roberta-base-squad2")
reader.warm_up() # Warm up the reader model


# إعداد pipeline
semantic_qa_pipeline = Pipeline()
semantic_qa_pipeline.add_component("text_embedder", text_embedder)
semantic_qa_pipeline.add_component("retriever", retriever)
semantic_qa_pipeline.add_component("reader", reader)

# Connect the components
semantic_qa_pipeline.connect("text_embedder.embedding", "retriever.query_embedding") # Connect the query embedding
semantic_qa_pipeline.connect("retriever", "reader")


# تنفيذ الاستعلام
query = "What are the effects of climate change?"
if chunks: # Only run the pipeline if there are documents
    # Prepare the data for the pipeline.
    # The documents with embeddings are already in the document store.
    result = semantic_qa_pipeline.run(data={
        "text_embedder": {"text": query}, # Pass the query to the embedder
        "retriever": {"top_k": 5}, # Pass top_k to the retriever
        "reader": {"query": query, "top_k": 2} # Pass query and top_k to the reader
    })

    # عرض النتائج
    if result and "reader" in result and "answers" in result["reader"]:
        for answer in result["reader"]["answers"]:
            # Access answer and score using dot notation
            print(f"- إجابة: {answer.answer} (الثقة: {answer.score:.2f})")
    else:
        print("No answers found.")
else:
    print("Pipeline not run due to no documents.")

NLTK punkt resource not found. Using regex for splitting.


[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Package punkt is already up-to-date!


Batches:   0%|          | 0/20 [00:00<?, ?it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

AttributeError: 'ExtractedAnswer' object has no attribute 'answer'

In [33]:
from haystack import Pipeline
from haystack.components.readers import ExtractiveReader
from haystack.components.retrievers.in_memory import InMemoryEmbeddingRetriever
from haystack.document_stores.in_memory import InMemoryDocumentStore
from haystack import Document

from sentence_transformers import SentenceTransformer
import re

# تحميل الكتاب من ملف نصي
with open("book.txt", "r", encoding="utf-8") as f:
    full_text = f.read()

# تقسيم شبه دلالي باستخدام طول النص
def split_semantic_chunks(text, max_words=100):
    sentences = re.split(r'(?<=[.!?])\s+', text)
    chunks = []
    current_chunk = ""
    for sentence in sentences:
        if not sentence.strip():
            continue
        if len((current_chunk + sentence).split()) > max_words:
            chunks.append(Document(content=current_chunk.strip()))
            current_chunk = sentence + " "
        else:
            current_chunk += sentence + " "
    if current_chunk.strip():
        chunks.append(Document(content=current_chunk.strip()))
    return chunks

# إنشاء المستندات
chunks = split_semantic_chunks(full_text, max_words=100)

# إعداد document store
document_store = InMemoryDocumentStore()
document_store.write_documents(chunks)

# تحميل نموذج embeddings
embedding_model = SentenceTransformer("sentence-transformers/all-MiniLM-L6-v2")

# إعداد retriever (بدون تمرير embedding_model مباشرة)
retriever = InMemoryEmbeddingRetriever()
retriever.embed_documents = lambda docs: embedding_model.encode([doc.content for doc in docs], convert_to_tensor=True)
retriever.embed_queries = lambda queries: embedding_model.encode(queries, convert_to_tensor=True)
retriever.warm_up(document_store)

# إعداد reader
reader = ExtractiveReader(model="deepset/roberta-base-squad2")

# إعداد pipeline
semantic_qa_pipeline = Pipeline()
semantic_qa_pipeline.add_component("retriever", retriever)
semantic_qa_pipeline.add_component("reader", reader)
semantic_qa_pipeline.connect("retriever", "reader")

# تنفيذ استعلام
query = "What are the effects of climate change?"
result = semantic_qa_pipeline.run(data={
    "retriever": {"query": query, "top_k": 5},
    "reader": {"query": query, "top_k": 2}
})

# عرض النتائج
for answer in result["reader"]["answers"]:
    print(f"- إجابة: {answer['answer']} (الثقة: {answer['score']:.2f})")


TypeError: InMemoryEmbeddingRetriever.__init__() missing 1 required positional argument: 'document_store'

In [34]:
from haystack import Pipeline
from haystack.components.readers import ExtractiveReader
from haystack.components.retrievers.in_memory import InMemoryEmbeddingRetriever
from haystack.document_stores.in_memory import InMemoryDocumentStore
from haystack import Document

from sentence_transformers import SentenceTransformer
import re

# تحميل الكتاب من ملف نصي
with open("book.txt", "r", encoding="utf-8") as f:
    full_text = f.read()

# تقسيم شبه دلالي إلى فقرات حسب عدد الكلمات
def split_semantic_chunks(text, max_words=100):
    sentences = re.split(r'(?<=[.!?])\s+', text)
    chunks = []
    current_chunk = ""
    for sentence in sentences:
        if not sentence.strip():
            continue
        if len((current_chunk + sentence).split()) > max_words:
            chunks.append(Document(content=current_chunk.strip()))
            current_chunk = sentence + " "
        else:
            current_chunk += sentence + " "
    if current_chunk.strip():
        chunks.append(Document(content=current_chunk.strip()))
    return chunks

# إنشاء المستندات
chunks = split_semantic_chunks(full_text, max_words=100)

# إعداد document store
document_store = InMemoryDocumentStore()
document_store.write_documents(chunks)

# تحميل نموذج التضمين (embedding)
embedding_model = SentenceTransformer("sentence-transformers/all-MiniLM-L6-v2")

# إعداد InMemoryEmbeddingRetriever وربطه بالـ document store
retriever = InMemoryEmbeddingRetriever(document_store=document_store)

# ربط دوال التضمين بالـ embedding model
retriever.embed_documents = lambda docs: embedding_model.encode([doc.content for doc in docs], convert_to_tensor=True)
retriever.embed_queries = lambda queries: embedding_model.encode(queries, convert_to_tensor=True)

# بناء الفهرس الداخلي
retriever.warm_up()

# إعداد القارئ (reader)
reader = ExtractiveReader(model="deepset/roberta-base-squad2")

# إنشاء pipeline
semantic_qa_pipeline = Pipeline()
semantic_qa_pipeline.add_component("retriever", retriever)
semantic_qa_pipeline.add_component("reader", reader)
semantic_qa_pipeline.connect("retriever", "reader")

# تنفيذ الاستعلام
query = "What are the effects of climate change?"
result = semantic_qa_pipeline.run(data={
    "retriever": {"query": query, "top_k": 5},
    "reader": {"query": query, "top_k": 2}
})

# عرض النتائج
for answer in result["reader"]["answers"]:
    print(f"- إجابة: {answer['answer']} (الثقة: {answer['score']:.2f})")


AttributeError: 'InMemoryEmbeddingRetriever' object has no attribute 'warm_up'

In [35]:
from haystack import Pipeline, Document
from haystack.components.readers import ExtractiveReader
from haystack.components.retrievers.in_memory import InMemoryEmbeddingRetriever
from haystack.document_stores.in_memory import InMemoryDocumentStore

from sentence_transformers import SentenceTransformer
import re

# تحميل الكتاب من ملف نصي
with open("book.txt", "r", encoding="utf-8") as f:
    full_text = f.read()

# تقسيم شبه دلالي للنص إلى فقرات (Chunks)
def split_semantic_chunks(text, max_words=100):
    sentences = re.split(r'(?<=[.!?])\s+', text)
    chunks = []
    current_chunk = ""
    for sentence in sentences:
        if not sentence.strip():
            continue
        if len((current_chunk + sentence).split()) > max_words:
            chunks.append(Document(content=current_chunk.strip()))
            current_chunk = sentence + " "
        else:
            current_chunk += sentence + " "
    if current_chunk.strip():
        chunks.append(Document(content=current_chunk.strip()))
    return chunks

# تقسيم النص إلى مستندات
chunks = split_semantic_chunks(full_text, max_words=100)

# إعداد document store
document_store = InMemoryDocumentStore()
document_store.write_documents(chunks)

# تحميل نموذج التضمين
embedding_model = SentenceTransformer("sentence-transformers/all-MiniLM-L6-v2")

# إعداد retriever وتوصيله بـ document store
retriever = InMemoryEmbeddingRetriever(document_store=document_store)

# ربط دوال التضمين
retriever.embed_documents = lambda docs: embedding_model.encode(
    [doc.content for doc in docs], convert_to_tensor=True
)
retriever.embed_queries = lambda queries: embedding_model.encode(
    queries, convert_to_tensor=True
)

# إعداد القارئ (reader)
reader = ExtractiveReader(model="deepset/roberta-base-squad2")

# بناء الـ Pipeline
pipeline = Pipeline()
pipeline.add_component("retriever", retriever)
pipeline.add_component("reader", reader)
pipeline.connect("retriever", "reader")

# الاستعلام
query = "What are the effects of climate change?"
result = pipeline.run(data={
    "retriever": {"query": query, "top_k": 5},
    "reader": {"query": query, "top_k": 2}
})

# عرض النتائج
for answer in result["reader"]["answers"]:
    print(f"- إجابة: {answer['answer']} (الثقة: {answer['score']:.2f})")


ValueError: Missing input for component retriever: query_embedding

In [37]:
from haystack import Pipeline, Document
from haystack.components.readers import ExtractiveReader
from haystack.components.retrievers.in_memory import InMemoryEmbeddingRetriever
from haystack.document_stores.in_memory import InMemoryDocumentStore

from sentence_transformers import SentenceTransformer
import re
import torch

# تحميل الكتاب من ملف نصي
with open("book.txt", "r", encoding="utf-8") as f:
    full_text = f.read()

# تقسيم النص شبه دلالي
def split_semantic_chunks(text, max_words=100):
    sentences = re.split(r'(?<=[.!?])\s+', text)
    chunks = []
    current_chunk = ""
    for sentence in sentences:
        if not sentence.strip():
            continue
        if len((current_chunk + sentence).split()) > max_words:
            chunks.append(Document(content=current_chunk.strip()))
            current_chunk = sentence + " "
        else:
            current_chunk += sentence + " "
    if current_chunk.strip():
        chunks.append(Document(content=current_chunk.strip()))
    return chunks

# إنشاء المستندات
chunks = split_semantic_chunks(full_text)

# إعداد التخزين
document_store = InMemoryDocumentStore()
document_store.write_documents(chunks)

# تحميل نموذج التضمين
embedding_model = SentenceTransformer("sentence-transformers/all-MiniLM-L6-v2")

# إعداد retriever
retriever = InMemoryEmbeddingRetriever(document_store=document_store)

# إعداد القارئ
reader = ExtractiveReader(model="deepset/roberta-base-squad2")

# إعداد الـ pipeline
pipeline = Pipeline()
pipeline.add_component("retriever", retriever)
pipeline.add_component("reader", reader)
pipeline.connect("retriever", "reader")

# الاستعلام
query = "What are the effects of climate change?"

# توليد التضمين للسؤال (query embedding)
#query_embedding = embedding_model.encode(query, convert_to_tensor=True)
#query_embedding = query_embedding.cpu().numpy()  # يجب أن يكون NumPy array
query_embedding = embedding_model.encode(query, convert_to_tensor=True)
query_embedding = query_embedding.cpu().numpy().tolist()

# تنفيذ الاستعلام باستخدام التضمين
result = pipeline.run(data={
    "retriever": {"query_embedding": query_embedding, "top_k": 5},
    "reader": {"query": query, "top_k": 2}
})

# عرض النتائج
for answer in result["reader"]["answers"]:
    print(f"- إجابة: {answer['answer']} (الثقة: {answer['score']:.2f})")


In [ ]:
# توليد التضمين للسؤال
query_embedding = embedding_model.encode(query, convert_to_tensor=True)
query_embedding = query_embedding.cpu().numpy().tolist()

# تحويل التضمين إلى list (كما تتطلبه Haystack)
query_embedding = query_embedding.cpu().numpy().tolist()


In [38]:
from haystack import Pipeline, Document
from haystack.components.readers import ExtractiveReader
from haystack.components.embedders.sentence_transformers import SentenceTransformersDocumentEmbedder, SentenceTransformersTextEmbedder
from haystack.components.retrievers.in_memory import InMemoryEmbeddingRetriever
from haystack.document_stores.in_memory import InMemoryDocumentStore
import re

# تحميل الكتاب من ملف نصي
with open("book.txt", "r", encoding="utf-8") as f:
    full_text = f.read()

# تقسيم شبه دلالي للنص إلى فقرات (Chunks)
def split_semantic_chunks(text, max_words=100):
    sentences = re.split(r'(?<=[.!?])\s+', text)
    chunks = []
    current_chunk = ""
    for sentence in sentences:
        if not sentence.strip():
            continue
        if len((current_chunk + sentence).split()) > max_words:
            chunks.append(Document(content=current_chunk.strip()))
            current_chunk = sentence + " "
        else:
            current_chunk += sentence + " "
    if current_chunk.strip():
        chunks.append(Document(content=current_chunk.strip()))
    return chunks

# تقسيم النص إلى مستندات
chunks = split_semantic_chunks(full_text, max_words=100)

# إعداد document store
document_store = InMemoryDocumentStore()

# إعداد embedder لتوليد embeddings للمستندات
doc_embedder = SentenceTransformersDocumentEmbedder(model="sentence-transformers/all-MiniLM-L6-v2")

# توليد embeddings للمستندات يدويًا
for doc in chunks:
    doc.embedding = doc_embedder.run(documents=[doc])["documents"][0].embedding

# تخزين المستندات بالتضمينات داخل الـ document store
document_store.write_documents(chunks)

# إعداد query embedder
query_embedder = SentenceTransformersTextEmbedder(model="sentence-transformers/all-MiniLM-L6-v2")

# إعداد retriever وربطه
retriever = InMemoryEmbeddingRetriever(document_store=document_store,
                                       document_embedder=None,  # لقد حسبناها يدويًا
                                       query_embedder=query_embedder)

# إعداد القارئ
reader = ExtractiveReader(model="deepset/roberta-base-squad2")

# إعداد pipeline
pipeline = Pipeline()
pipeline.add_component("retriever", retriever)
pipeline.add_component("reader", reader)
pipeline.connect("retriever", "reader")

# تنفيذ استعلام
query = "What are the effects of climate change?"
result = pipeline.run(data={
    "retriever": {"query": query, "top_k": 5},
    "reader": {"query": query, "top_k": 2}
})

# عرض النتائج
for answer in result["reader"]["answers"]:
    print(f"- إجابة: {answer['answer']} (الثقة: {answer['score']:.2f})")


ModuleNotFoundError: No module named 'haystack.components.embedders.sentence_transformers'

In [39]:
!pip install "farm-haystack>=2.0.0"


ERROR: Could not find a version that satisfies the requirement farm-haystack>=2.0.0 (from versions: 0.1.0.post2, 0.2.0.post1, 0.2.1, 0.3.0, 0.4.0, 0.5.0, 0.6.0, 0.7.0, 0.8.0, 0.9.0, 0.10.0, 1.0.0, 1.1.0, 1.2.0, 1.3.0, 1.4.0, 1.5.0, 1.6.0, 1.7.0, 1.7.1, 1.8.0, 1.9.0rc1, 1.9.0rc2, 1.9.0rc3, 1.9.0, 1.9.1rc1, 1.9.1, 1.10.0rc1, 1.10.0, 1.11.0rc0, 1.11.0, 1.11.1rc1, 1.11.1, 1.12.0rc1, 1.12.0rc2, 1.12.0, 1.12.1, 1.12.2rc1, 1.12.2, 1.13.0rc1, 1.13.0rc2, 1.13.0, 1.13.1rc1, 1.13.1, 1.13.2rc0, 1.13.2, 1.14.0rc1, 1.14.0rc2, 1.14.0, 1.15.0rc1, 1.15.0rc2, 1.15.0rc3, 1.15.0rc4, 1.15.0rc5, 1.15.0, 1.15.1rc1, 1.15.1, 1.16.0rc1, 1.16.0rc2, 1.16.0, 1.16.1rc1, 1.16.1, 1.17.0rc1, 1.17.0rc2, 1.17.0, 1.17.1, 1.17.2rc1, 1.17.2, 1.18.0rc1, 1.18.0rc2, 1.18.0, 1.18.1, 1.19.0rc1, 1.19.0rc2, 1.19.0, 1.20.0rc1, 1.20.0, 1.20.1, 1.20.2rc0, 1.21.0rc0, 1.21.0rc1, 1.21.0, 1.21.1rc1, 1.21.1rc2, 1.21.1, 1.21.2rc1, 1.21.2, 1.22.0rc0, 1.22.0rc1, 1.22.0rc2, 1.22.0rc3, 1.22.0, 1.22.1, 1.23.0rc0, 1.23.0rc1, 1.23.0, 1.24.0rc1, 

In [40]:
!pip uninstall -y farm-haystack
!pip install git+https://github.com/deepset-ai/haystack.git@main

  Cloning https://github.com/deepset-ai/haystack.git (to revision main) to /tmp/pip-req-build-b3k38yax
  Running command git clone --filter=blob:none --quiet https://github.com/deepset-ai/haystack.git /tmp/pip-req-build-b3k38yax
  Resolved https://github.com/deepset-ai/haystack.git to commit 7dbac5b3c9f7810058ad97bf02abf94a73454679
  Installing build dependencies ... done
  Getting requirements to build wheel ... done
  Preparing metadata (pyproject.toml) ... done
  Created wheel for haystack-ai: filename=haystack_ai-2.15.0rc0-py3-none-any.whl size=523706 sha256=170e6caefa828bb5933a5998aff1bd1d6930ae3a175b7f9db973cb69f6bb084b
  Stored in directory: /tmp/pip-ephem-wheel-cache-kbkww_vg/wheels/b1/48/49/19ff23db8ee37ab13155d169607bf99ee3d13fc90877af4437
Successfully built haystack-ai
  Attempting uninstall: haystack-ai
    Found existing installation: haystack-ai 2.14.2
    Uninstalling haystack-ai-2.14.2:
      Successfully uninstalled haystack-ai-2.14.2


In [1]:
import haystack
print(haystack.__version__)


2.15.0rc0


In [3]:
!pip uninstall -y farm-haystack


In [4]:
!pip install git+https://github.com/deepset-ai/haystack.git@main


  Cloning https://github.com/deepset-ai/haystack.git (to revision main) to /tmp/pip-req-build-shxgx4ge
  Running command git clone --filter=blob:none --quiet https://github.com/deepset-ai/haystack.git /tmp/pip-req-build-shxgx4ge
  Resolved https://github.com/deepset-ai/haystack.git to commit 7dbac5b3c9f7810058ad97bf02abf94a73454679
  Installing build dependencies ... done
  Getting requirements to build wheel ... done
  Preparing metadata (pyproject.toml) ... done


In [1]:
from haystack import Pipeline, Document
from haystack.components.readers import ExtractiveReader
from haystack.components.embedders.sentence_transformers import (
    SentenceTransformersDocumentEmbedder,
    SentenceTransformersTextEmbedder
)
from haystack.components.retrievers.in_memory import InMemoryEmbeddingRetriever
from haystack.document_stores.in_memory import InMemoryDocumentStore
import re

# 1. تحميل الكتاب من ملف نصي
with open("book.txt", "r", encoding="utf-8") as f:
    full_text = f.read()

# 2. تقسيم الكتاب إلى chunks دلالية (ليست جمل فقط)
def split_semantic_chunks(text, max_words=100):
    sentences = re.split(r'(?<=[.!?])\s+', text)
    chunks = []
    current_chunk = ""
    for sentence in sentences:
        if not sentence.strip():
            continue
        if len((current_chunk + sentence).split()) > max_words:
            chunks.append(Document(content=current_chunk.strip()))
            current_chunk = sentence + " "
        else:
            current_chunk += sentence + " "
    if current_chunk.strip():
        chunks.append(Document(content=current_chunk.strip()))
    return chunks

chunks = split_semantic_chunks(full_text)

# 3. إعداد document store وتضمين المستندات
document_store = InMemoryDocumentStore()
doc_embedder = SentenceTransformersDocumentEmbedder(model="sentence-transformers/all-MiniLM-L6-v2")
for doc in chunks:
    doc.embedding = doc_embedder.run(documents=[doc])["documents"][0].embedding

document_store.write_documents(chunks)

# 4. إعداد retriever والقارئ
query_embedder = SentenceTransformersTextEmbedder(model="sentence-transformers/all-MiniLM-L6-v2")
retriever = InMemoryEmbeddingRetriever(document_store=document_store, document_embedder=None, query_embedder=query_embedder)
reader = ExtractiveReader(model="deepset/roberta-base-squad2")

# 5. إنشاء pipeline
pipeline = Pipeline()
pipeline.add_component("retriever", retriever)
pipeline.add_component("reader", reader)
pipeline.connect("retriever", "reader")

# 6. تنفيذ سؤال
query = "What are the effects of climate change?"
result = pipeline.run(data={
    "retriever": {"query": query, "top_k": 5},
    "reader": {"query": query, "top_k": 2}
})

# 7. عرض النتائج
for answer in result["reader"]["answers"]:
    print(f"- إجابة: {answer['answer']} (الثقة: {answer['score']:.2f})")


ModuleNotFoundError: No module named 'haystack.components.embedders.sentence_transformers'

In [1]:
import haystack
print(haystack.__version__)


2.15.0rc0


In [3]:
!pip install git+https://github.com/deepset-ai/haystack.git

  Cloning https://github.com/deepset-ai/haystack.git to /tmp/pip-req-build-qx_sd1if
  Running command git clone --filter=blob:none --quiet https://github.com/deepset-ai/haystack.git /tmp/pip-req-build-qx_sd1if
  Resolved https://github.com/deepset-ai/haystack.git to commit 7dbac5b3c9f7810058ad97bf02abf94a73454679
  Installing build dependencies ... done
  Getting requirements to build wheel ... done
  Preparing metadata (pyproject.toml) ... done


In [2]:
from haystack import Pipeline, Document
from haystack.components.readers import ExtractiveReader
from haystack.components.embedders import SentenceTransformersDocumentEmbedder, SentenceTransformersTextEmbedder
from haystack.components.retrievers.in_memory import InMemoryEmbeddingRetriever
from haystack.document_stores.in_memory import InMemoryDocumentStore
import re

# 1. Load the book from a text file
with open("book.txt", "r", encoding="utf-8") as f:
    full_text = f.read()

# 2. Split the book into semantic chunks (not just sentences)
def split_semantic_chunks(text, max_words=100):
    sentences = re.split(r'(?<=[.!?])\s+', text)
    chunks = []
    current_chunk = ""
    for sentence in sentences:
        if not sentence.strip():
            continue
        if len((current_chunk + sentence).split()) > max_words:
            chunks.append(Document(content=current_chunk.strip()))
            current_chunk = sentence + " "
        else:
            current_chunk += sentence + " "
    if current_chunk.strip():
        chunks.append(Document(content=current_chunk.strip()))
    return chunks

chunks = split_semantic_chunks(full_text)

# 3. Set up document store and embed documents
document_store = InMemoryDocumentStore()
doc_embedder = SentenceTransformersDocumentEmbedder(model="sentence-transformers/all-MiniLM-L6-v2")
for doc in chunks:
    doc.embedding = doc_embedder.run(documents=[doc])["documents"][0].embedding

document_store.write_documents(chunks)

# 4. Set up retriever and reader
query_embedder = SentenceTransformersTextEmbedder(model="sentence-transformers/all-MiniLM-L6-v2")
retriever = InMemoryEmbeddingRetriever(document_store=document_store)
reader = ExtractiveReader(model="deepset/roberta-base-squad2")

# 5. Create pipeline
pipeline = Pipeline()
pipeline.add_component("retriever", retriever)
pipeline.add_component("reader", reader)
pipeline.connect("retriever", "reader")

# 6. Execute a query
query = "What are the effects of climate change?"
result = pipeline.run(data={
    "retriever": {"query": query, "top_k": 5},
    "reader": {"query": query, "top_k": 2}
})

# 7. Display results
for answer in result["reader"]["answers"]:
    print(f"- Answer: {answer['answer']} (Confidence: {answer['score']:.2f})")

RuntimeError: The embedding model has not been loaded. Please call warm_up() before running.

In [3]:
!pip show haystack-ai

Name: haystack-ai
Version: 2.15.0rc0
Summary: LLM framework to build customizable, production-ready LLM applications. Connect components (models, vector DBs, file converters) to pipelines or agents that can interact with your data.
Home-page: https://github.com/deepset-ai/haystack
Author: 
Author-email: "deepset.ai" <malte.pietsch@deepset.ai>
License: 
Location: /usr/local/lib/python3.11/dist-packages
Requires: docstring-parser, haystack-experimental, jinja2, jsonschema, lazy-imports, more-itertools, networkx, numpy, openai, posthog, pydantic, python-dateutil, pyyaml, requests, tenacity, tqdm, typing-extensions
Required-by: haystack-experimental


In [ ]:
!pip install --upgrade haystack-ai



In [4]:
from haystack import Pipeline, Document
from haystack.components.readers import ExtractiveReader
from haystack.components.embedders import SentenceTransformersDocumentEmbedder, SentenceTransformersTextEmbedder
from haystack.components.retrievers.in_memory import InMemoryEmbeddingRetriever
from haystack.document_stores.in_memory import InMemoryDocumentStore
import re

# 1. Load the book from a text file
with open("book.txt", "r", encoding="utf-8") as f:
    full_text = f.read()

# 2. Split the book into semantic chunks (not just sentences)
def split_semantic_chunks(text, max_words=100):
    sentences = re.split(r'(?<=[.!?])\s+', text)
    chunks = []
    current_chunk = ""
    for sentence in sentences:
        if not sentence.strip():
            continue
        if len((current_chunk + sentence).split()) > max_words:
            chunks.append(Document(content=current_chunk.strip()))
            current_chunk = sentence + " "
        else:
            current_chunk += sentence + " "
    if current_chunk.strip():
        chunks.append(Document(content=current_chunk.strip()))
    return chunks

chunks = split_semantic_chunks(full_text)

# 3. Set up document store and embed documents
document_store = InMemoryDocumentStore()

# Initialize and warm up the document embedder
doc_embedder = SentenceTransformersDocumentEmbedder(model="sentence-transformers/all-MiniLM-L6-v2")
doc_embedder.warm_up()  # This loads the model

# Embed documents and write to store
embedded_docs = []
for doc in chunks:
    # Create a copy of the document to avoid modifying the original
    doc_copy = Document(content=doc.content, meta=doc.meta)
    embedding_result = doc_embedder.run(documents=[doc_copy])
    doc_copy.embedding = embedding_result["documents"][0].embedding
    embedded_docs.append(doc_copy)

document_store.write_documents(embedded_docs)

# 4. Set up retriever and reader
query_embedder = SentenceTransformersTextEmbedder(model="sentence-transformers/all-MiniLM-L6-v2")
query_embedder.warm_up()  # This loads the model

retriever = InMemoryEmbeddingRetriever(document_store=document_store)
reader = ExtractiveReader(model="deepset/roberta-base-squad2")
reader.warm_up()  # This loads the reader model

# 5. Create pipeline
pipeline = Pipeline()
pipeline.add_component("text_embedder", query_embedder)
pipeline.add_component("retriever", retriever)
pipeline.add_component("reader", reader)

# Connect the components correctly
pipeline.connect("text_embedder.embedding", "retriever.query_embedding")
pipeline.connect("retriever", "reader")

# 6. Execute a query
query = "What are the effects of climate change?"
result = pipeline.run({
    "text_embedder": {"text": query},
    "retriever": {"top_k": 5},
    "reader": {"query": query, "top_k": 2}
})

# 7. Display results
for answer in result["reader"]["answers"]:
    print(f"- Answer: {answer['answer']} (Confidence: {answer['score']:.2f})")

/usr/local/lib/python3.11/dist-packages/huggingface_hub/utils/_auth.py:94: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

...

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

TypeError: 'ExtractedAnswer' object is not subscriptable

### شغال

In [5]:
from haystack import Pipeline, Document
from haystack.components.readers import ExtractiveReader
from haystack.components.embedders import SentenceTransformersDocumentEmbedder, SentenceTransformersTextEmbedder
from haystack.components.retrievers.in_memory import InMemoryEmbeddingRetriever
from haystack.document_stores.in_memory import InMemoryDocumentStore
import re

# 1. Load the book from a text file
with open("book.txt", "r", encoding="utf-8") as f:
    full_text = f.read()

# 2. Split the book into semantic chunks (not just sentences)
def split_semantic_chunks(text, max_words=100):
    sentences = re.split(r'(?<=[.!?])\s+', text)
    chunks = []
    current_chunk = ""
    for sentence in sentences:
        if not sentence.strip():
            continue
        if len((current_chunk + sentence).split()) > max_words:
            chunks.append(Document(content=current_chunk.strip()))
            current_chunk = sentence + " "
        else:
            current_chunk += sentence + " "
    if current_chunk.strip():
        chunks.append(Document(content=current_chunk.strip()))
    return chunks

chunks = split_semantic_chunks(full_text)

# 3. Set up document store and embed documents
document_store = InMemoryDocumentStore()

# Initialize and warm up the document embedder
doc_embedder = SentenceTransformersDocumentEmbedder(model="sentence-transformers/all-MiniLM-L6-v2")
doc_embedder.warm_up()

# Embed documents and write to store
embedded_docs = []
for doc in chunks:
    doc_copy = Document(content=doc.content, meta=doc.meta)
    embedding_result = doc_embedder.run(documents=[doc_copy])
    doc_copy.embedding = embedding_result["documents"][0].embedding
    embedded_docs.append(doc_copy)

document_store.write_documents(embedded_docs)

# 4. Set up retriever and reader
query_embedder = SentenceTransformersTextEmbedder(model="sentence-transformers/all-MiniLM-L6-v2")
query_embedder.warm_up()

retriever = InMemoryEmbeddingRetriever(document_store=document_store)
reader = ExtractiveReader(model="deepset/roberta-base-squad2")
reader.warm_up()

# 5. Create pipeline
pipeline = Pipeline()
pipeline.add_component("text_embedder", query_embedder)
pipeline.add_component("retriever", retriever)
pipeline.add_component("reader", reader)

pipeline.connect("text_embedder.embedding", "retriever.query_embedding")
pipeline.connect("retriever.documents", "reader.documents")

# 6. Execute a query
query = "What are the effects of climate change?"
result = pipeline.run({
    "text_embedder": {"text": query},
    "retriever": {"top_k": 5},
    "reader": {"query": query, "top_k": 2}
})

# 7. Display results - properly accessing ExtractedAnswer attributes
print(f"Question: {query}")
print("Answers:")
for answer in result["reader"]["answers"]:
    print(f"- {answer.data} (Confidence: {answer.score:.2f})")
    print(f"  Context: {answer.context}\n")

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

...

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Question: What are the effects of climate change?
Answers:
- damage to infrastructure, reduced agricultural 
productivity, health care costs, and lost labor productivity (Confidence: 0.76)
  Context: None

- Rising Temperatures (Confidence: 0.69)
  Context: None

- None (Confidence: 0.07)
  Context: None



### شغال

In [1]:
from haystack import Pipeline, Document
from haystack.components.readers import ExtractiveReader
from haystack.components.embedders import SentenceTransformersDocumentEmbedder, SentenceTransformersTextEmbedder
from haystack.components.retrievers.in_memory import InMemoryEmbeddingRetriever
from haystack.document_stores.in_memory import InMemoryDocumentStore
import re

# 1. Load the book from a text file
with open("book.txt", "r", encoding="utf-8") as f:
    full_text = f.read()

# 2. Split the book into semantic chunks (not just sentences)
def split_semantic_chunks(text, max_words=100):
    sentences = re.split(r'(?<=[.!?])\s+', text)
    chunks = []
    current_chunk = ""
    for sentence in sentences:
        if not sentence.strip():
            continue
        if len((current_chunk + sentence).split()) > max_words:
            chunks.append(Document(content=current_chunk.strip()))
            current_chunk = sentence + " "
        else:
            current_chunk += sentence + " "
    if current_chunk.strip():
        chunks.append(Document(content=current_chunk.strip()))
    return chunks

chunks = split_semantic_chunks(full_text)

# 3. Set up document store and embed documents
document_store = InMemoryDocumentStore()

# Initialize and warm up the document embedder
doc_embedder = SentenceTransformersDocumentEmbedder(model="sentence-transformers/all-MiniLM-L6-v2")
doc_embedder.warm_up()

# Embed documents and write to store
embedded_docs = []
for doc in chunks:
    doc_copy = Document(content=doc.content, meta=doc.meta)
    embedding_result = doc_embedder.run(documents=[doc_copy])
    doc_copy.embedding = embedding_result["documents"][0].embedding
    embedded_docs.append(doc_copy)

document_store.write_documents(embedded_docs)

# 4. Set up retriever and reader
query_embedder = SentenceTransformersTextEmbedder(model="sentence-transformers/all-MiniLM-L6-v2")
query_embedder.warm_up()

retriever = InMemoryEmbeddingRetriever(document_store=document_store)
reader = ExtractiveReader(model="deepset/roberta-base-squad2")
reader.warm_up()

# 5. Create pipeline
pipeline = Pipeline()
pipeline.add_component("text_embedder", query_embedder)
pipeline.add_component("retriever", retriever)
pipeline.add_component("reader", reader)

pipeline.connect("text_embedder.embedding", "retriever.query_embedding")
pipeline.connect("retriever.documents", "reader.documents")

# 6. Execute a query
query = "What are the causes of climate change as stated in the context?"
result = pipeline.run({
    "text_embedder": {"text": query},
    "retriever": {"top_k": 5},
    "reader": {"query": query, "top_k": 2}
})

# 7. Display results - properly accessing ExtractedAnswer attributes
print(f"Question: {query}")
print("Answers:")
for answer in result["reader"]["answers"]:
    print(f"- {answer.data} (Confidence: {answer.score:.2f})")
    print(f"  Context: {answer.context}\n")

/usr/local/lib/python3.11/dist-packages/huggingface_hub/utils/_auth.py:94: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

...

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Question: What are the causes of climate change as stated in the context?
Answers:
- burning of fossil fuels and deforestation (Confidence: 0.73)
  Context: None

- damage to infrastructure, reduced agricultural 
productivity, health care costs, and lost labor productivity (Confidence: 0.70)
  Context: None

- None (Confidence: 0.08)
  Context: None



In [1]:
from haystack import Pipeline, Document
from haystack.components.readers import ExtractiveReader
from haystack.components.embedders import SentenceTransformersDocumentEmbedder, SentenceTransformersTextEmbedder
from haystack.components.retrievers.in_memory import InMemoryEmbeddingRetriever
from haystack.document_stores.in_memory import InMemoryDocumentStore
from nltk.tokenize import sent_tokenize
import re

# 1. Improved text loading with error handling
try:
    with open("book.txt", "r", encoding="utf-8") as f:
        full_text = f.read()
except Exception as e:
    print(f"Error loading file: {e}")
    exit()

# 2. Enhanced semantic chunking
def split_semantic_chunks(text, max_words=150):
    sentences = sent_tokenize(text)
    chunks = []
    current_chunk = []
    current_length = 0

    for sentence in sentences:
        sentence_length = len(sentence.split())
        if current_length + sentence_length > max_words and current_chunk:
            chunks.append(" ".join(current_chunk))
            current_chunk = [sentence]
            current_length = sentence_length
        else:
            current_chunk.append(sentence)
            current_length += sentence_length

    if current_chunk:
        chunks.append(" ".join(current_chunk))

    return [Document(content=chunk, meta={"chunk_id": i}) for i, chunk in enumerate(chunks)]

# 3. Enhanced document processing
document_store = InMemoryDocumentStore()

# Initialize with better model parameters
doc_embedder = SentenceTransformersDocumentEmbedder(
    model="sentence-transformers/all-mpnet-base-v2",  # More powerful model
    device="cpu",  # or "cuda" if available
    batch_size=32
)
doc_embedder.warm_up()

# Process documents in batches
chunks = split_semantic_chunks(full_text)
for i in range(0, len(chunks), 32):
    batch = chunks[i:i+32]
    embeddings = doc_embedder.run(documents=batch)["documents"]
    for doc, emb in zip(batch, embeddings):
        doc.embedding = emb.embedding
    document_store.write_documents(batch)

# 4. Enhanced query processing
query_embedder = SentenceTransformersTextEmbedder(
    model="sentence-transformers/all-mpnet-base-v2",
    device="cpu"
)
query_embedder.warm_up()

retriever = InMemoryEmbeddingRetriever(
    document_store=document_store,
    top_k=10,  # Retrieve more documents for better recall
    scale_score=True
)

reader = ExtractiveReader(
    model="deepset/roberta-base-squad2",
    top_k_per_candidate=3,
    max_seq_length=384,
    device="cpu"
)
reader.warm_up()

# 5. Enhanced pipeline with better connections
pipeline = Pipeline()
pipeline.add_component("text_embedder", query_embedder)
pipeline.add_component("retriever", retriever)
pipeline.add_component("reader", reader)

pipeline.connect("text_embedder.embedding", "retriever.query_embedding")
pipeline.connect("retriever.documents", "reader.documents")

# 6. Execute query with better parameters
query = "What are the primary causes of climate change mentioned in the text?"
result = pipeline.run({
    "text_embedder": {"text": query},
    "retriever": {"top_k": 10},
    "reader": {
        "query": query,
        "top_k": 3,
        "confidence_threshold": 0.65  # Filter low-confidence answers
    }
})

# 7. Enhanced results display
def clean_text(text):
    return re.sub(r'\s+', ' ', text).strip()

print(f"\nQuestion: {query}")
print("="*50)

answers = [ans for ans in result["reader"]["answers"] if ans.score >= 0.65 and ans.data]
if not answers:
    print("No confident answers found.")
else:
    for i, answer in enumerate(answers, 1):
        context = clean_text(answer.context or answer.document.content)
        print(f"\nAnswer #{i} (Confidence: {answer.score:.2f}):")
        print(f"- {clean_text(answer.data)}")
        print(f"\nContext: {context[:500]}...\n")
        print("-"*50)

ValueError: Invalid component device type 'str'. Must either be None or ComponentDevice.

In [2]:
from haystack import Pipeline, Document
from haystack.components.readers import ExtractiveReader
from haystack.components.embedders import SentenceTransformersDocumentEmbedder, SentenceTransformersTextEmbedder
from haystack.components.retrievers.in_memory import InMemoryEmbeddingRetriever
from haystack.document_stores.in_memory import InMemoryDocumentStore
from haystack.utils import ComponentDevice
from nltk.tokenize import sent_tokenize
import re

# 1. Improved text loading with error handling
try:
    with open("book.txt", "r", encoding="utf-8") as f:
        full_text = f.read()
except Exception as e:
    print(f"Error loading file: {e}")
    exit()

# 2. Enhanced semantic chunking
def split_semantic_chunks(text, max_words=150):
    sentences = sent_tokenize(text)
    chunks = []
    current_chunk = []
    current_length = 0

    for sentence in sentences:
        sentence_length = len(sentence.split())
        if current_length + sentence_length > max_words and current_chunk:
            chunks.append(" ".join(current_chunk))
            current_chunk = [sentence]
            current_length = sentence_length
        else:
            current_chunk.append(sentence)
            current_length += sentence_length

    if current_chunk:
        chunks.append(" ".join(current_chunk))

    return [Document(content=chunk, meta={"chunk_id": i}) for i, chunk in enumerate(chunks)]

# Initialize device (CPU or GPU if available)
#device = ComponentDevice.from_str("cuda:0")  # or "cpu"
device = ComponentDevice.from_str("cpu")
# 3. Enhanced document processing
document_store = InMemoryDocumentStore()

# Initialize with proper device handling
doc_embedder = SentenceTransformersDocumentEmbedder(
    model="sentence-transformers/all-mpnet-base-v2",
    device=device,  # Correct device parameter
    batch_size=32
)
doc_embedder.warm_up()

# Process documents
chunks = split_semantic_chunks(full_text)
for i in range(0, len(chunks), 32):
    batch = chunks[i:i+32]
    embeddings = doc_embedder.run(documents=batch)["documents"]
    for doc, emb in zip(batch, embeddings):
        doc.embedding = emb.embedding
    document_store.write_documents(batch)

# 4. Enhanced query processing
query_embedder = SentenceTransformersTextEmbedder(
    model="sentence-transformers/all-mpnet-base-v2",
    device=device  # Correct device parameter
)
query_embedder.warm_up()

retriever = InMemoryEmbeddingRetriever(
    document_store=document_store,
    top_k=10,
    scale_score=True
)

reader = ExtractiveReader(
    model="deepset/roberta-base-squad2",
    top_k_per_candidate=3,
    max_seq_length=384,
    device=device  # Correct device parameter
)
reader.warm_up()

# 5. Pipeline setup (same as before)
pipeline = Pipeline()
pipeline.add_component("text_embedder", query_embedder)
pipeline.add_component("retriever", retriever)
pipeline.add_component("reader", reader)

pipeline.connect("text_embedder.embedding", "retriever.query_embedding")
pipeline.connect("retriever.documents", "reader.documents")

# 6. Query execution
query = "What are the primary causes of climate change mentioned in the text?"
result = pipeline.run({
    "text_embedder": {"text": query},
    "retriever": {"top_k": 10},
    "reader": {
        "query": query,
        "top_k": 3,
        "confidence_threshold": 0.65
    }
})

# 7. Results display
def clean_text(text):
    return re.sub(r'\s+', ' ', text).strip()

print(f"\nQuestion: {query}")
print("="*50)

answers = [ans for ans in result["reader"]["answers"] if ans.score >= 0.65 and ans.data]
if not answers:
    print("No confident answers found.")
else:
    for i, answer in enumerate(answers, 1):
        context = clean_text(answer.context or answer.document.content)
        print(f"\nAnswer #{i} (Confidence: {answer.score:.2f}):")
        print(f"- {clean_text(answer.data)}")
        print(f"\nContext: {context[:500]}...\n")
        print("-"*50)

LookupError: 
**********************************************************************
  Resource [93mpunkt_tab[0m not found.
  Please use the NLTK Downloader to obtain the resource:

  [31m>>> import nltk
  >>> nltk.download('punkt_tab')
  [0m
  For more information see: https://www.nltk.org/data.html

  Attempted to load [93mtokenizers/punkt_tab/english/[0m

  Searched in:
    - '/root/nltk_data'
    - '/usr/nltk_data'
    - '/usr/share/nltk_data'
    - '/usr/lib/nltk_data'
    - '/usr/share/nltk_data'
    - '/usr/local/share/nltk_data'
    - '/usr/lib/nltk_data'
    - '/usr/local/lib/nltk_data'
**********************************************************************


In [1]:
from haystack import Pipeline, Document
from haystack.components.readers import ExtractiveReader
from haystack.components.embedders import SentenceTransformersDocumentEmbedder, SentenceTransformersTextEmbedder
from haystack.components.retrievers.in_memory import InMemoryEmbeddingRetriever
from haystack.document_stores.in_memory import InMemoryDocumentStore
from haystack.utils import ComponentDevice
from nltk.tokenize import sent_tokenize
import re
import nltk # Import nltk

# 1. تحميل بيانات NLTK المطلوبة
# Check if punkt is available, download if not. If not, try punkt_tab as per error message.
try:
    nltk.data.find('tokenizers/punkt')
except LookupError:
    try:
        print("تحميل بيانات تقسيم الجمل (punkt)...")
        nltk.download('punkt')
    except LookupError:
        try:
            print("تحميل بيانات تقسيم الجمل (punkt_tab) كما هو مطلوب في الخطأ...")
            nltk.download('punkt_tab')
        except Exception as e:
            print(f"فشل تحميل بيانات NLTK: {e}")


# 2. تحميل النص مع معالجة الأخطاء
try:
    with open("book.txt", "r", encoding="utf-8") as f:
        full_text = f.read()
except FileNotFoundError:
    print("خطأ: ملف book.txt غير موجود")
    exit()
except Exception as e:
    print(f"حدث خطأ أثناء قراءة الملف: {e}")
    exit()

# 3. تقسيم النص إلى أجزاء دلالية محسنة
def split_semantic_chunks(text, max_words=150):
    try:
        sentences = sent_tokenize(text)
    except Exception as e:
        print(f"خطأ في تقسيم الجمل باستخدام NLTK: {e}")
        sentences = re.split(r'(?<=[.!?])\s+', text)  # استخدام بديل إذا فشل NLTK

    chunks = []
    current_chunk = []
    current_length = 0

    for sentence in sentences:
        sentence_words = sentence.split()
        sentence_length = len(sentence_words)

        if current_length + sentence_length > max_words and current_chunk:
            chunks.append(" ".join(current_chunk))
            current_chunk = [sentence]
            current_length = sentence_length
        else:
            current_chunk.append(sentence)
            current_length += sentence_length

    if current_chunk:
        chunks.append(" ".join(current_chunk))

    return [Document(content=chunk.strip(), meta={"chunk_id": i}) for i, chunk in enumerate(chunks)]

# 4. إعداد الجهاز
try:
    # Use ComponentDevice.from_literal
    device = ComponentDevice.from_literal("cuda:0") if 'cuda' in ComponentDevice.get_available_devices() else ComponentDevice.from_literal("cpu")
except Exception as e:
    print(f"خطأ في إعداد الجهاز: {e}")
    device = None  # استخدام الإعداد الافتراضي

# 5. معالجة المستندات
document_store = InMemoryDocumentStore()

try:
    doc_embedder = SentenceTransformersDocumentEmbedder(
        model="sentence-transformers/all-mpnet-base-v2",
        device=device,
        batch_size=16  # تقليل حجم الدفعة لتجنب مشاكل الذاكرة
    )
    doc_embedder.warm_up()
except Exception as e:
    print(f"خطأ في تحميل نموذج التضمين: {e}")
    exit()

# 6. تقسيم النص وتضمينه
try:
    chunks = split_semantic_chunks(full_text)
    if chunks:
        for i in range(0, len(chunks), 16):  # دفعات أصغر لتجنب نفاد الذاكرة
            batch = chunks[i:i+16]
            embeddings = doc_embedder.run(documents=batch)["documents"]
            for doc, emb in zip(batch, embeddings):
                doc.embedding = emb.embedding
            document_store.write_documents(batch)
except Exception as e:
    print(f"خطأ في معالجة المستندات: {e}")
    exit()

# 7. إعداد مكونات الاستعلام
try:
    query_embedder = SentenceTransformersTextEmbedder(
        model="sentence-transformers/all-mpnet-base-v2",
        device=device
    )
    query_embedder.warm_up()

    retriever = InMemoryEmbeddingRetriever(
        document_store=document_store,
        top_k=5,  # تقليل عدد المستندات المسترجعة
        scale_score=True
    )
    # No warm_up needed for InMemoryEmbeddingRetriever

    reader = ExtractiveReader(
        model="deepset/roberta-base-squad2",
        top_k_per_candidate=2,
        max_seq_length=384,
        device=device
    )
    reader.warm_up()
except Exception as e:
    print(f"خطأ في إعداد مكونات الاستعلام: {e}")
    exit()

# 8. إنشاء خط المعالجة
pipeline = Pipeline()
pipeline.add_component("text_embedder", query_embedder)
pipeline.add_component("retriever", retriever)
pipeline.add_component("reader", reader)

pipeline.connect("text_embedder.embedding", "retriever.query_embedding")
pipeline.connect("retriever", "reader") # Corrected connection


# 9. تنفيذ الاستعلام
def ask_question(question):
    if not document_store.count_documents():
        return "Document store is empty. Cannot answer questions."

    try:
        result = pipeline.run(data={
            "text_embedder": {"text": question},
            "retriever": {"top_k": 5},
            "reader": {
                "query": question,
                "top_k": 2,
                "confidence_threshold": 0.7  # زيادة عتبة الثقة
            }
        })

        answers = [ans for ans in result["reader"]["answers"] if ans.score >= 0.7 and ans.data]
        if not answers:
            return "لم أجد إجابات ذات ثقة كافية في النص."

        # Fixed SyntaxError in the return statement
        return "\n\n".join(
            f"الإجابة {i+1} (الثقة: {ans.score:.2f}):\n{ans.data}\n\nالسياق:\n{ans.document.content[:300]}..."
            for i, ans in enumerate(answers)
        ) # Added closing parenthesis
    except Exception as e:
        return f"حدث خطأ أثناء معالجة السؤال: {e}"

# 10. مثال على الاستخدام
if __name__ == "__main__":
    question = "What are the main causes of climate change?"
    print(ask_question(question))

خطأ في إعداد الجهاز: type object 'ComponentDevice' has no attribute 'get_available_devices'


/usr/local/lib/python3.11/dist-packages/huggingface_hub/utils/_auth.py:94: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


خطأ في تقسيم الجمل باستخدام NLTK: 
**********************************************************************
  Resource punkt_tab not found.
  Please use the NLTK Downloader to obtain the resource:

  >>> import nltk
  >>> nltk.download('punkt_tab')
  
  For more information see: https://www.nltk.org/data.html

  Attempted to load tokenizers/punkt_tab/english/

  Searched in:
    - '/root/nltk_data'
    - '/usr/nltk_data'
    - '/usr/share/nltk_data'
    - '/usr/lib/nltk_data'
    - '/usr/share/nltk_data'
    - '/usr/local/share/nltk_data'
    - '/usr/lib/nltk_data'
    - '/usr/local/lib/nltk_data'
**********************************************************************



Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

خطأ في إعداد مكونات الاستعلام: ExtractiveReader.__init__() got an unexpected keyword argument 'top_k_per_candidate'


NameError: name 'reader' is not defined

In [1]:
from haystack import Pipeline, Document
from haystack.components.readers import ExtractiveReader
from haystack.components.embedders import SentenceTransformersDocumentEmbedder, SentenceTransformersTextEmbedder
from haystack.components.retrievers.in_memory import InMemoryEmbeddingRetriever
from haystack.document_stores.in_memory import InMemoryDocumentStore
from haystack.utils import ComponentDevice
from nltk.tokenize import sent_tokenize
import re

# 1. تحميل بيانات NLTK المطلوبة
try:
    nltk.data.find('tokenizers/punkt')
except LookupError:
    print("تحميل بيانات تقسيم الجمل...")
    nltk.download('punkt')

# 2. تحميل النص مع معالجة الأخطاء
try:
    with open("book.txt", "r", encoding="utf-8") as f:
        full_text = f.read()
except FileNotFoundError:
    print("خطأ: ملف book.txt غير موجود")
    exit()
except Exception as e:
    print(f"حدث خطأ أثناء قراءة الملف: {e}")
    exit()

# 3. تقسيم النص إلى أجزاء دلالية محسنة
def split_semantic_chunks(text, max_words=150):
    try:
        sentences = sent_tokenize(text)
    except Exception as e:
        print(f"خطأ في تقسيم الجمل: {e}")
        sentences = re.split(r'(?<=[.!?])\s+', text)  # استخدام بديل إذا فشل NLTK

    chunks = []
    current_chunk = []
    current_length = 0

    for sentence in sentences:
        sentence_words = sentence.split()
        sentence_length = len(sentence_words)

        if current_length + sentence_length > max_words and current_chunk:
            chunks.append(" ".join(current_chunk))
            current_chunk = [sentence]
            current_length = sentence_length
        else:
            current_chunk.append(sentence)
            current_length += sentence_length

    if current_chunk:
        chunks.append(" ".join(current_chunk))

    return [Document(content=chunk.strip(), meta={"chunk_id": i}) for i, chunk in enumerate(chunks)]

# 4. إعداد الجهاز
try:
    device = ComponentDevice.from_str("cuda:0") if torch.cuda.is_available() else ComponentDevice.from_str("cpu")
except:
    device = None  # استخدام الإعداد الافتراضي

# 5. معالجة المستندات
document_store = InMemoryDocumentStore()

try:
    doc_embedder = SentenceTransformersDocumentEmbedder(
        model="sentence-transformers/all-mpnet-base-v2",
        device=device,
        batch_size=16  # تقليل حجم الدفعة لتجنب مشاكل الذاكرة
    )
    doc_embedder.warm_up()
except Exception as e:
    print(f"خطأ في تحميل نموذج التضمين: {e}")
    exit()

# 6. تقسيم النص وتضمينه
try:
    chunks = split_semantic_chunks(full_text)
    for i in range(0, len(chunks), 16):  # دفعات أصغر لتجنب نفاد الذاكرة
        batch = chunks[i:i+16]
        embeddings = doc_embedder.run(documents=batch)["documents"]
        for doc, emb in zip(batch, embeddings):
            doc.embedding = emb.embedding
        document_store.write_documents(batch)
except Exception as e:
    print(f"خطأ في معالجة المستندات: {e}")
    exit()

# 7. إعداد مكونات الاستعلام
try:
    query_embedder = SentenceTransformersTextEmbedder(
        model="sentence-transformers/all-mpnet-base-v2",
        device=device
    )
    query_embedder.warm_up()

    retriever = InMemoryEmbeddingRetriever(
        document_store=document_store,
        top_k=5,  # تقليل عدد المستندات المسترجعة
        scale_score=True
    )

    reader = ExtractiveReader(
        model="deepset/roberta-base-squad2",
        top_k_per_candidate=2,
        max_seq_length=384,
        device=device
    )
    reader.warm_up()
except Exception as e:
    print(f"خطأ في إعداد مكونات الاستعلام: {e}")
    exit()

# 8. إنشاء خط المعالجة
pipeline = Pipeline()
pipeline.add_component("text_embedder", query_embedder)
pipeline.add_component("retriever", retriever)
pipeline.add_component("reader", reader)

pipeline.connect("text_embedder.embedding", "retriever.query_embedding")
pipeline.connect("retriever.documents", "reader.documents")

# 9. تنفيذ الاستعلام
def ask_question(question):
    try:
        result = pipeline.run({
            "text_embedder": {"text": question},
            "retriever": {"top_k": 5},
            "reader": {
                "query": question,
                "top_k": 2,
                "confidence_threshold": 0.7  # زيادة عتبة الثقة
            }
        })

        answers = [ans for ans in result["reader"]["answers"] if ans.score >= 0.7 and ans.data]
        if not answers:
            return "لم أجد إجابات ذات ثقة كافية في النص."

        return "\n\n".join(
            f"الإجابة {i+1} (الثقة: {ans.score:.2f}):\n{ans.data}\n\nالسياق:\n{ans.document.content[:300]}..."
            for i, ans in enumerate(answers)
    except Exception as e:
        return f"حدث خطأ أثناء معالجة السؤال: {e}"

# 10. مثال على الاستخدام
if __name__ == "__main__":
    question = "ما هي الأسباب الرئيسية لتغير المناخ؟"
    print(ask_question(question))

SyntaxError: '(' was never closed (<ipython-input-1-1565844524>, line 141)

In [2]:
!pip install pdfminer.six

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 5.6/5.6 MB 27.8 MB/s eta 0:00:00


In [4]:
from haystack.components.converters import PDFMinerToDocument
from datetime import datetime # Import datetime

converter = PDFMinerToDocument()
results = converter.run(sources=["sample.pdf"], meta={"date_added": datetime.now().isoformat()})
documents = results["documents"]

print(documents[0].content)

# 'This is a text from the PDF file.'



Understanding Climate Change 


Chapter 1: Introduction to Climate Change 


Climate change refers to significant, long-term changes in the global climate. The term 
"global climate" encompasses the planet's overall weather patterns, including temperature, 
precipitation, and wind patterns, over an extended period. Over the past century, human 
activities, particularly the burning of fossil fuels and deforestation, have significantly 
contributed to climate change. 


Historical Context 


The Earth's climate has changed throughout history. Over the past 650,000 years, there have 
been seven cycles of glacial advance and retreat, with the abrupt end of the last ice age about 
11,700 years ago marking the beginning of the modern climate era and human civilization. 
Most of these climate changes are attributed to very small variations in Earth's orbit that 
change the amount of solar energy our planet receives. During the Holocene epoch, which 
began at the end of the last ice age, hum

In [6]:
from haystack.components.converters import PDFMinerToDocument
from haystack.document_stores.in_memory import InMemoryDocumentStore
from haystack.components.preprocessors import DocumentCleaner
from haystack.components.preprocessors import DocumentSplitter
from haystack.components.writers import DocumentWriter
from haystack import Pipeline # Import Pipeline

document_store = InMemoryDocumentStore()

pipeline = Pipeline()
pipeline.add_component("converter", PDFMinerToDocument())
pipeline.add_component("cleaner", DocumentCleaner())
pipeline.add_component("splitter", DocumentSplitter(split_by="sentence", split_length=5))
pipeline.add_component("writer", DocumentWriter(document_store=document_store))
pipeline.connect("converter", "cleaner")
pipeline.connect("cleaner", "splitter")
pipeline.connect("splitter", "writer")

# Define the file_names variable
file_names = ["sample.pdf"] # Replace with your PDF file names

pipeline.run({"converter": {"sources": file_names}})

# Optional: Verify documents are written to the store
print(f"Number of documents in store: {document_store.count_documents()}")

[nltk_data] Downloading package punkt_tab to /root/nltk_data...
[nltk_data]   Unzipping tokenizers/punkt_tab.zip.


Number of documents in store: 63


https://docs.haystack.deepset.ai/docs/pdfminertodocument

In [7]:
embedder = SentenceTransformersDocumentEmbedder(model="intfloat/e5-large-v2",
                                                prefix="passage")

NameError: name 'SentenceTransformersDocumentEmbedder' is not defined

In [8]:
from haystack import Document
from haystack.components.embedders import SentenceTransformersDocumentEmbedder

doc = Document(content="some text",
               meta={"title": "relevant title",
                         "page number": 18})

embedder = SentenceTransformersDocumentEmbedder(meta_fields_to_embed=["title"])

docs_w_embeddings = embedder.run(documents=[doc])["documents"]

RuntimeError: The embedding model has not been loaded. Please call warm_up() before running.

In [9]:
from haystack import Document
from haystack.components.embedders import SentenceTransformersDocumentEmbedder
doc = Document(content="I love pizza!")
doc_embedder = SentenceTransformersDocumentEmbedder()
doc_embedder.warm_up()

result = doc_embedder.run([doc])
print(result['documents'][0].embedding)

# [-0.07804739475250244, 0.1498992145061493, ...]

/usr/local/lib/python3.11/dist-packages/huggingface_hub/utils/_auth.py:94: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


Batches:   0%|          | 0/1 [00:00<?, ?it/s]

[-0.07804738730192184, 0.14989922940731049, -0.00031763484003022313, 0.016943739727139473, 0.048198409378528595, 0.02771099843084812, -0.05298449471592903, 0.042614106088876724, 0.031863514333963394, 0.0013959900243207812, -0.03700629621744156, 0.0025032497942447662, -0.02511141635477543, 0.08638107031583786, -0.03845543414354324, 0.001582351978868246, 0.02800198644399643, 0.028474627062678337, 0.05593224987387657, 0.039229247719049454, -0.006626022048294544, 0.02720414288341999, -0.03692684322595596, -0.04708828032016754, -0.05724935978651047, -0.008639605715870857, -0.008555501699447632, -0.02418375387787819, 0.0028049778193235397, 0.05014966055750847, -0.006754754576832056, 0.02595985308289528, -0.010146334767341614, 0.012081758119165897, 1.534563352834084e-06, 0.003300305688753724, -0.018832415342330933, 0.03670321777462959, -0.04240981861948967, 0.045924123376607895, -0.004215971101075411, -0.05211002752184868, -0.05693129822611809, -0.03482379391789436, -0.00587291968986392, 0.07

In [10]:
from haystack import Document
from haystack import Pipeline
from haystack.document_stores.in_memory import InMemoryDocumentStore
from haystack.components.embedders import SentenceTransformersTextEmbedder, SentenceTransformersDocumentEmbedder
from haystack.components.writers import DocumentWriter
from haystack.components.retrievers.in_memory import InMemoryEmbeddingRetriever

document_store = InMemoryDocumentStore(embedding_similarity_function="cosine")

documents = [Document(content="My name is Wolfgang and I live in Berlin"),
             Document(content="I saw a black horse running"),
             Document(content="Germany has many big cities")]

indexing_pipeline = Pipeline()
indexing_pipeline.add_component("embedder", SentenceTransformersDocumentEmbedder())
indexing_pipeline.add_component("writer", DocumentWriter(document_store=document_store))
indexing_pipeline.connect("embedder", "writer")

query_pipeline = Pipeline()
query_pipeline.add_component("text_embedder", SentenceTransformersTextEmbedder())
query_pipeline.add_component("retriever", InMemoryEmbeddingRetriever(document_store=document_store))
query_pipeline.connect("text_embedder.embedding", "retriever.query_embedding")

query = "Who lives in Berlin?"

indexing_pipeline.run({"documents": documents})
result = query_pipeline.run({"text_embedder":{"text": query}})

print(result['retriever']['documents'][0])

# Document(id=..., mimetype: 'text/plain',
#  text: 'My name is Wolfgang and I live in Berlin')

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Document(id=62fad790ad2af927af9432c87330ed2ea5e31332cdec8e9d6235a5105ab0aaf5, content: 'My name is Wolfgang and I live in Berlin', score: 0.5515620199247835)


In [ ]:
from haystack.components.generators.chat import HuggingFaceLocalChatGenerator
from haystack.dataclasses import ChatMessage

generator = HuggingFaceLocalChatGenerator(model="HuggingFaceH4/zephyr-7b-beta")
generator.warm_up()
messages = [ChatMessage.from_user("What's Natural Language Processing? Be brief.")]
print(generator.run(messages))

In [17]:
!huggingface-cli login --token XXXX

The token has not been saved to the git credentials helper. Pass `add_to_git_credential=True` in this function directly or `--add-to-git-credential` if using via `huggingface-cli` if you want to set the git credential as well.
Token is valid (permission: read).
The token `read` has been saved to /root/.cache/huggingface/stored_tokens
Your token has been saved to /root/.cache/huggingface/token
Login successful.
The current active token is: `read`


In [ ]:
from haystack.components.generators.chat import HuggingFaceLocalChatGenerator
from haystack.dataclasses import ChatMessage

generator = HuggingFaceLocalChatGenerator(model="meta-llama/Llama-3.2-1B-Instruct")
generator.warm_up()
messages = [ChatMessage.from_user("What's Natural Language Processing? Be brief.")]
print(generator.run(messages))

https://docs.haystack.deepset.ai/docs/huggingfacelocalchatgenerator

In [24]:
from haystack import Pipeline
from haystack.components.generators.chat import HuggingFaceLocalChatGenerator
from haystack.dataclasses import ChatMessage
#from haystack.components.generators.builders import ChatMessageBuilder
from haystack.components.generators.chat import HuggingFaceLocalChatGenerator
from haystack.dataclasses import ChatMessage
from haystack.utils import Secret

# Use ChatMessageBuilder
#prompt_builder = ChatMessageBuilder()
#llm = HuggingFaceLocalChatGenerator(model="meta-llama/Llama-3.2-1B-Instruct", token=Secret.from_env_var("HF_API_TOKEN"))

# Warm up the LLM
llm.warm_up()

pipe = Pipeline()
pipe.add_component("prompt_builder", prompt_builder)
pipe.add_component("llm", llm)
pipe.connect("prompt_builder.prompt", "llm.messages")
location = "Berlin"
messages = [ChatMessage.from_system("Always respond in German even if some input data is in other languages."),
            ChatMessage.from_user("Tell me about {{location}}")]
pipe.run(data={"prompt_builder": {"template_variables":{"location": location}, "template": messages}})

NameError: name 'llm' is not defined

In [ ]:
from haystack.components.generators import HuggingFaceLocalGenerator

generator = HuggingFaceLocalGenerator(model="google/flan-t5-large",
                                      task="text2text-generation",
                                      generation_kwargs={
                                        "max_new_tokens": 100,
                                        "temperature": 0.9,
                                        })

generator.warm_up()
print(generator.run("Who is the best American actor?"))
# {'replies': ['john wayne']}

https://docs.haystack.deepset.ai/docs/huggingfacelocalgenerator

In [ ]:
from haystack import Pipeline
from haystack.components.retrievers.in_memory import InMemoryBM25Retriever
from haystack.components.builders.prompt_builder import PromptBuilder
from haystack.components.generators import HuggingFaceLocalGenerator
from haystack.document_stores.in_memory import InMemoryDocumentStore
from haystack import Document

docstore = InMemoryDocumentStore()
docstore.write_documents([Document(content="Rome is the capital of Italy"), Document(content="Paris is the capital of France")])

generator = HuggingFaceLocalGenerator(model="google/flan-t5-large",
                                      task="text2text-generation",
                                      generation_kwargs={
                                        "max_new_tokens": 100,
                                        "temperature": 0.9,
                                        })

query = "What is the capital of France?"

template = """
Given the following information, answer the question.

Context:
{% for document in documents %}
    {{ document.content }}
{% endfor %}

Question: {{ query }}?
"""
pipe = Pipeline()

pipe.add_component("retriever", InMemoryBM25Retriever(document_store=docstore))
pipe.add_component("prompt_builder", PromptBuilder(template=template))
pipe.add_component("llm", generator)
pipe.connect("retriever", "prompt_builder.documents")
pipe.connect("prompt_builder", "llm")

res=pipe.run({
    "prompt_builder": {
        "query": query
    },
    "retriever": {
        "query": query
    }
})

print(res)

### شغال

In [25]:
from haystack.components.generators import HuggingFaceLocalGenerator

generator = HuggingFaceLocalGenerator(model="meta-llama/Llama-3.2-1B-Instruct",
                                      task="text2text-generation",
                                      generation_kwargs={
                                        "max_new_tokens": 100,
                                        "temperature": 0.9,
                                        })

generator.warm_up()
print(generator.run("Who is the best American actor?"))
# {'replies': ['john wayne']}

Device set to use cpu
The model 'LlamaForCausalLM' is not supported for text2text-generation. Supported models are ['PeftModelForSeq2SeqLM', 'BartForConditionalGeneration', 'BigBirdPegasusForConditionalGeneration', 'BlenderbotForConditionalGeneration', 'BlenderbotSmallForConditionalGeneration', 'EncoderDecoderModel', 'FSMTForConditionalGeneration', 'GPTSanJapaneseForConditionalGeneration', 'GraniteSpeechForConditionalGeneration', 'LEDForConditionalGeneration', 'LongT5ForConditionalGeneration', 'M2M100ForConditionalGeneration', 'MarianMTModel', 'MBartForConditionalGeneration', 'MT5ForConditionalGeneration', 'MvpForConditionalGeneration', 'NllbMoeForConditionalGeneration', 'PegasusForConditionalGeneration', 'PegasusXForConditionalGeneration', 'PLBartForConditionalGeneration', 'ProphetNetForConditionalGeneration', 'Qwen2AudioForConditionalGeneration', 'SeamlessM4TForTextToText', 'SeamlessM4Tv2ForTextToText', 'SwitchTransformersForConditionalGeneration', 'T5ForConditionalGeneration', 'UMT5

{'replies': ['Who is the best American actor? There is no definitive answer to this question, as opinions on the best American actor vary widely depending on personal taste, cultural context, and historical period. However, here are some of the most highly regarded American actors of all time:\n\n1. Marlon Brando (1924-2004): Known for his iconic roles in "A Streetcar Named Desire" and "The Godfather," Brando is widely regarded as one of the greatest actors of all time.\n2. Daniel Day-Lewis:']}


In [1]:
from haystack import Pipeline, Document
from haystack.components.readers import ExtractiveReader
from haystack.components.embedders import SentenceTransformersDocumentEmbedder, SentenceTransformersTextEmbedder
from haystack.components.retrievers.in_memory import InMemoryEmbeddingRetriever
from haystack.document_stores.in_memory import InMemoryDocumentStore
from haystack.utils import ComponentDevice
import re
import torch

# 1. تحميل النص مع معالجة الأخطاء
try:
    with open("book.txt", "r", encoding="utf-8") as f:
        full_text = f.read()
except FileNotFoundError:
    print("خطأ: ملف book.txt غير موجود")
    exit()
except Exception as e:
    print(f"حدث خطأ أثناء قراءة الملف: {e}")
    exit()

# 2. تقسيم النص إلى أجزاء دلالية باستخدام regex فقط
def split_semantic_chunks(text, max_words=150):
    # تقسيم النص إلى جمل باستخدام regex
    sentences = re.split(r'(?<=[.!?])\s+', text)

    chunks = []
    current_chunk = []
    current_length = 0

    for sentence in sentences:
        sentence_words = sentence.split()
        sentence_length = len(sentence_words)

        if current_length + sentence_length > max_words and current_chunk:
            chunks.append(" ".join(current_chunk))
            current_chunk = [sentence]
            current_length = sentence_length
        else:
            current_chunk.append(sentence)
            current_length += sentence_length

    if current_chunk:
        chunks.append(" ".join(current_chunk))

    return [Document(content=chunk.strip(), meta={"chunk_id": i}) for i, chunk in enumerate(chunks)]

# 3. إعداد الجهاز
try:
    device = ComponentDevice.from_str("cuda:0") if torch.cuda.is_available() else ComponentDevice.from_str("cpu")
except:
    device = None  # استخدام الإعداد الافتراضي

# 4. معالجة المستندات
document_store = InMemoryDocumentStore()

try:
    doc_embedder = SentenceTransformersDocumentEmbedder(
        model="sentence-transformers/all-mpnet-base-v2",
        device=device,
        batch_size=16
    )
    doc_embedder.warm_up()
except Exception as e:
    print(f"خطأ في تحميل نموذج التضمين: {e}")
    exit()

# 5. تقسيم النص وتضمينه
try:
    chunks = split_semantic_chunks(full_text)
    for i in range(0, len(chunks), 16):
        batch = chunks[i:i+16]
        embeddings = doc_embedder.run(documents=batch)["documents"]
        for doc, emb in zip(batch, embeddings):
            doc.embedding = emb.embedding
        document_store.write_documents(batch)
except Exception as e:
    print(f"خطأ في معالجة المستندات: {e}")
    exit()

# 6. إعداد مكونات الاستعلام
try:
    query_embedder = SentenceTransformersTextEmbedder(
        model="sentence-transformers/all-mpnet-base-v2",
        device=device
    )
    query_embedder.warm_up()

    retriever = InMemoryEmbeddingRetriever(
        document_store=document_store,
        top_k=5,
        scale_score=True
    )

    reader = ExtractiveReader(
        model="deepset/roberta-base-squad2",
        top_k_per_candidate=2,
        max_seq_length=384,
        device=device
    )
    reader.warm_up()
except Exception as e:
    print(f"خطأ في إعداد مكونات الاستعلام: {e}")
    exit()

# 7. إنشاء خط المعالجة
pipeline = Pipeline()
pipeline.add_component("text_embedder", query_embedder)
pipeline.add_component("retriever", retriever)
pipeline.add_component("reader", reader)

pipeline.connect("text_embedder.embedding", "retriever.query_embedding")
pipeline.connect("retriever.documents", "reader.documents")

# 8. دالة لطرح الأسئلة
def ask_question(question):
    try:
        result = pipeline.run({
            "text_embedder": {"text": question},
            "retriever": {"top_k": 5},
            "reader": {
                "query": question,
                "top_k": 2,
                "confidence_threshold": 0.7
            }
        })

        answers = [ans for ans in result["reader"]["answers"] if ans.score >= 0.7 and ans.data]
        if not answers:
            return "لم أجد إجابات ذات ثقة كافية في النص."

        output = []
        for i, ans in enumerate(answers):
            answer_text = f"الإجابة {i+1} (الثقة: {ans.score:.2f}):\n{ans.data}"
            context = ans.document.content[:300] + "..." if ans.document.content else "لا يوجد سياق"
            output.append(f"{answer_text}\n\nالسياق:\n{context}")

        return "\n\n".join(output)
    except Exception as e:
        return f"حدث خطأ أثناء معالجة السؤال: {e}"

# 9. مثال على الاستخدام
if __name__ == "__main__":
    question = "What are the main causes of climate change?"
    print(ask_question(question))

/usr/local/lib/python3.11/dist-packages/huggingface_hub/utils/_auth.py:94: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

خطأ في إعداد مكونات الاستعلام: ExtractiveReader.__init__() got an unexpected keyword argument 'top_k_per_candidate'


NameError: name 'reader' is not defined

In [1]:
from haystack import Pipeline, Document
from haystack.components.readers import ExtractiveReader
from haystack.components.embedders import SentenceTransformersDocumentEmbedder, SentenceTransformersTextEmbedder
from haystack.components.retrievers.in_memory import InMemoryEmbeddingRetriever
from haystack.document_stores.in_memory import InMemoryDocumentStore
from haystack.utils import ComponentDevice
import re
import torch

# 1. تحميل النص
try:
    with open("book.txt", "r", encoding="utf-8") as f:
        full_text = f.read()
except Exception as e:
    print(f"خطأ في قراءة الملف: {e}")
    exit()

# 2. تقسيم النص إلى أجزاء
def split_semantic_chunks(text, max_words=150):
    sentences = re.split(r'(?<=[.!?])\s+', text)
    chunks = []
    current_chunk = []
    current_length = 0

    for sentence in sentences:
        words = sentence.split()
        if current_length + len(words) > max_words and current_chunk:
            chunks.append(" ".join(current_chunk))
            current_chunk = [sentence]
            current_length = len(words)
        else:
            current_chunk.append(sentence)
            current_length += len(words)

    if current_chunk:
        chunks.append(" ".join(current_chunk))

    return [Document(content=chunk.strip()) for chunk in chunks]

# 3. إعداد الجهاز
device = ComponentDevice.from_str("cuda" if torch.cuda.is_available() else "cpu")

# 4. تضمين المستندات
document_store = InMemoryDocumentStore()
doc_embedder = SentenceTransformersDocumentEmbedder(
    model="sentence-transformers/all-mpnet-base-v2",
    device=device
)
doc_embedder.warm_up()

chunks = split_semantic_chunks(full_text)
for i in range(0, len(chunks), 8):  # حجم دفعة أصغر
    batch = chunks[i:i+8]
    embeddings = doc_embedder.run(documents=batch)["documents"]
    for doc, emb in zip(batch, embeddings):
        doc.embedding = emb.embedding
    document_store.write_documents(batch)

# 5. إعداد مكونات الاستعلام
query_embedder = SentenceTransformersTextEmbedder(
    model="sentence-transformers/all-mpnet-base-v2",
    device=device
)
query_embedder.warm_up()

retriever = InMemoryEmbeddingRetriever(
    document_store=document_store,
    top_k=5
)

# تصحيح تعريف القارئ هنا
reader = ExtractiveReader(
    model="deepset/roberta-base-squad2",
    top_k=2,  # تم تغيير من top_k_per_candidate إلى top_k
    device=device
)
reader.warm_up()

# 6. بناء خط المعالجة
pipeline = Pipeline()
pipeline.add_component("text_embedder", query_embedder)
pipeline.add_component("retriever", retriever)
pipeline.add_component("reader", reader)

pipeline.connect("text_embedder.embedding", "retriever.query_embedding")
pipeline.connect("retriever.documents", "reader.documents")

# 7. دالة لطرح الأسئلة
def ask_question(question):
    try:
        result = pipeline.run({
            "text_embedder": {"text": question},
            "retriever": {"top_k": 5},
            "reader": {
                "query": question,
                "top_k": 2,
                "confidence_threshold": 0.65
            }
        })

        answers = [ans for ans in result["reader"]["answers"] if ans.score >= 0.65]
        if not answers:
            return "لا توجد إجابات ذات ثقة كافية"

        return "\n\n".join(
            f"الإجابة {i+1} (الثقة: {ans.score:.2f}):\n{ans.data}\n\nالسياق:\n{ans.document.content[:300]}..."
            for i, ans in enumerate(answers)
    except Exception as e:
        return f"خطأ: {e}"

# 8. اختبار النظام
if __name__ == "__main__":
    while True:
        question = input("\nادخل سؤالك (أو 'exit' للخروج): ")
        if question.lower() == 'exit':
            break
        print(ask_question(question))

SyntaxError: '(' was never closed (<ipython-input-1-3437260857>, line 105)

In [2]:
from haystack import Pipeline, Document
from haystack.components.readers import ExtractiveReader
from haystack.components.embedders import SentenceTransformersDocumentEmbedder, SentenceTransformersTextEmbedder
from haystack.components.retrievers.in_memory import InMemoryEmbeddingRetriever
from haystack.document_stores.in_memory import InMemoryDocumentStore
from haystack.utils import ComponentDevice
import re
import torch

# 1. تحميل النص
try:
    with open("book.txt", "r", encoding="utf-8") as f:
        full_text = f.read()
except Exception as e:
    print(f"خطأ في قراءة الملف: {e}")
    exit()

# 2. تقسيم النص إلى أجزاء
def split_semantic_chunks(text, max_words=150):
    sentences = re.split(r'(?<=[.!?])\s+', text)
    chunks = []
    current_chunk = []
    current_length = 0

    for sentence in sentences:
        words = sentence.split()
        if current_length + len(words) > max_words and current_chunk:
            chunks.append(" ".join(current_chunk))
            current_chunk = [sentence]
            current_length = len(words)
        else:
            current_chunk.append(sentence)
            current_length += len(words)

    if current_chunk:
        chunks.append(" ".join(current_chunk))

    return [Document(content=chunk.strip()) for chunk in chunks]

# 3. إعداد الجهاز
device = ComponentDevice.from_str("cuda" if torch.cuda.is_available() else "cpu")

# 4. تضمين المستندات
document_store = InMemoryDocumentStore()
doc_embedder = SentenceTransformersDocumentEmbedder(
    model="sentence-transformers/all-mpnet-base-v2",
    device=device
)
doc_embedder.warm_up()

chunks = split_semantic_chunks(full_text)
for i in range(0, len(chunks), 8):  # حجم دفعة أصغر
    batch = chunks[i:i+8]
    embeddings = doc_embedder.run(documents=batch)["documents"]
    for doc, emb in zip(batch, embeddings):
        doc.embedding = emb.embedding
    document_store.write_documents(batch)

# 5. إعداد مكونات الاستعلام
query_embedder = SentenceTransformersTextEmbedder(
    model="sentence-transformers/all-mpnet-base-v2",
    device=device
)
query_embedder.warm_up()

retriever = InMemoryEmbeddingRetriever(
    document_store=document_store,
    top_k=5
)

reader = ExtractiveReader(
    model="deepset/roberta-base-squad2",
    top_k=2,
    device=device
)
reader.warm_up()

# 6. بناء خط المعالجة
pipeline = Pipeline()
pipeline.add_component("text_embedder", query_embedder)
pipeline.add_component("retriever", retriever)
pipeline.add_component("reader", reader)

pipeline.connect("text_embedder.embedding", "retriever.query_embedding")
pipeline.connect("retriever.documents", "reader.documents")

# 7. دالة لطرح الأسئلة - تم تصحيح الأقواس هنا
def ask_question(question):
    try:
        result = pipeline.run({
            "text_embedder": {"text": question},
            "retriever": {"top_k": 5},
            "reader": {
                "query": question,
                "top_k": 2,
                "confidence_threshold": 0.65
            }
        })

        answers = [ans for ans in result["reader"]["answers"] if ans.score >= 0.65]
        if not answers:
            return "لا توجد إجابات ذات ثقة كافية"

        output = []
        for i, ans in enumerate(answers):
            answer_text = f"الإجابة {i+1} (الثقة: {ans.score:.2f}):\n{ans.data}"
            context = ans.document.content[:300] + "..." if ans.document.content else "لا يوجد سياق"
            output.append(f"{answer_text}\n\nالسياق:\n{context}")

        return "\n\n".join(output)  # تم إغلاق الأقواس بشكل صحيح هنا
    except Exception as e:
        return f"خطأ: {e}"

# 8. اختبار النظام
if __name__ == "__main__":
    while True:
        question = input("\nادخل سؤالك (أو 'exit' للخروج): ")
        if question.lower() == 'exit':
            break
        print(ask_question(question))

/usr/local/lib/python3.11/dist-packages/huggingface_hub/utils/_auth.py:94: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

...

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]


ادخل سؤالك (أو 'exit' للخروج): What are the main causes of climate change?
خطأ: Input confidence_threshold not found in component reader.

ادخل سؤالك (أو 'exit' للخروج): exit


In [3]:
from haystack import Pipeline, Document
from haystack.components.readers import ExtractiveReader
from haystack.components.embedders import SentenceTransformersDocumentEmbedder, SentenceTransformersTextEmbedder
from haystack.components.retrievers.in_memory import InMemoryEmbeddingRetriever
from haystack.document_stores.in_memory import InMemoryDocumentStore
from haystack.utils import ComponentDevice
import re
import torch

# 1. تحميل النص
try:
    with open("book.txt", "r", encoding="utf-8") as f:
        full_text = f.read()
except Exception as e:
    print(f"خطأ في قراءة الملف: {e}")
    exit()

# 2. تقسيم النص إلى أجزاء
def split_semantic_chunks(text, max_words=150):
    sentences = re.split(r'(?<=[.!?])\s+', text)
    chunks = []
    current_chunk = []
    current_length = 0

    for sentence in sentences:
        words = sentence.split()
        if current_length + len(words) > max_words and current_chunk:
            chunks.append(" ".join(current_chunk))
            current_chunk = [sentence]
            current_length = len(words)
        else:
            current_chunk.append(sentence)
            current_length += len(words)

    if current_chunk:
        chunks.append(" ".join(current_chunk))

    return [Document(content=chunk.strip()) for chunk in chunks]

# 3. إعداد الجهاز
device = ComponentDevice.from_str("cuda" if torch.cuda.is_available() else "cpu")

# 4. تضمين المستندات
document_store = InMemoryDocumentStore()
doc_embedder = SentenceTransformersDocumentEmbedder(
    model="sentence-transformers/all-mpnet-base-v2",
    device=device
)
doc_embedder.warm_up()

chunks = split_semantic_chunks(full_text)
for i in range(0, len(chunks), 8):  # حجم دفعة أصغر
    batch = chunks[i:i+8]
    embeddings = doc_embedder.run(documents=batch)["documents"]
    for doc, emb in zip(batch, embeddings):
        doc.embedding = emb.embedding
    document_store.write_documents(batch)

# 5. إعداد مكونات الاستعلام
query_embedder = SentenceTransformersTextEmbedder(
    model="sentence-transformers/all-mpnet-base-v2",
    device=device
)
query_embedder.warm_up()

retriever = InMemoryEmbeddingRetriever(
    document_store=document_store,
    top_k=5
)

reader = ExtractiveReader(
    model="deepset/roberta-base-squad2",
    top_k=2,
    device=device
)
reader.warm_up()

# 6. بناء خط المعالجة
pipeline = Pipeline()
pipeline.add_component("text_embedder", query_embedder)
pipeline.add_component("retriever", retriever)
pipeline.add_component("reader", reader)

pipeline.connect("text_embedder.embedding", "retriever.query_embedding")
pipeline.connect("retriever.documents", "reader.documents")

# 7. دالة لطرح الأسئلة - تم تصحيح الأقواس هنا
def ask_question(question):
    try:
        result = pipeline.run({
            "text_embedder": {"text": question},
            "retriever": {"top_k": 5},
            "reader": {
                "query": question,
                "top_k": 2,
                "confidence_threshold": 0.65
            }
        })

        answers = [ans for ans in result["reader"]["answers"] if ans.score >= 0.65]
        if not answers:
            return "لا توجد إجابات ذات ثقة كافية"

        output = []
        for i, ans in enumerate(answers):
            answer_text = f"الإجابة {i+1} (الثقة: {ans.score:.2f}):\n{ans.data}"
            context = ans.document.content[:300] + "..." if ans.document.content else "لا يوجد سياق"
            output.append(f"{answer_text}\n\nالسياق:\n{context}")

        return "\n\n".join(output)  # تم إغلاق الأقواس بشكل صحيح هنا
    except Exception as e:
        return f"خطأ: {e}"

# 8. اختبار النظام
if __name__ == "__main__":
    while True:
        question = input("\nادخل سؤالك (أو 'exit' للخروج): ")
        if question.lower() == 'exit':
            break
        print(ask_question(question))

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]


ادخل سؤالك (أو 'exit' للخروج): what is Climate Change?
خطأ: Input confidence_threshold not found in component reader.

ادخل سؤالك (أو 'exit' للخروج): exit


In [ ]:
Climate Change

In [1]:
from haystack import Pipeline
from haystack.components.embedders import SentenceTransformersDocumentEmbedder, SentenceTransformersTextEmbedder
from haystack.components.retrievers.in_memory import InMemoryEmbeddingRetriever
from haystack.components.readers import ExtractiveReader
from haystack.document_stores.in_memory import InMemoryDocumentStore
from haystack import Document
import re

def load_and_chunk_text(file_path, chunk_size=150):
    """تحميل النص وتقسيمه إلى أجزاء دلالية"""
    try:
        with open(file_path, "r", encoding="utf-8") as f:
            text = f.read()
    except Exception as e:
        print(f"خطأ في قراءة الملف: {e}")
        return None

    # تقسيم النص مع الحفاظ على السياق
    sentences = re.split(r'(?<=[.!?])\s+', text)
    chunks = []
    current_chunk = []
    word_count = 0

    for sentence in sentences:
        words = sentence.split()
        num_words = len(words)

        if word_count + num_words > chunk_size and current_chunk:
            chunks.append(" ".join(current_chunk))
            current_chunk = [sentence]
            word_count = num_words
        else:
            current_chunk.append(sentence)
            word_count += num_words

    if current_chunk:
        chunks.append(" ".join(current_chunk))

    return [Document(content=chunk.strip()) for chunk in chunks]

def initialize_qa_system():
    """تهيئة نظام السؤال والإجابة"""
    # 1. إنشاء مستودع المستندات
    document_store = InMemoryDocumentStore()

    # 2. تقسيم النص إلى أجزاء
    documents = load_and_chunk_text("book.txt")
    if not documents:
        return None

    # 3. تضمين المستندات
    doc_embedder = SentenceTransformersDocumentEmbedder(
        model="sentence-transformers/all-mpnet-base-v2"
    )
    doc_embedder.warm_up()

    # معالجة المستندات على دفعات
    batch_size = 16
    for i in range(0, len(documents), batch_size):
        batch = documents[i:i+batch_size]
        result = doc_embedder.run(batch)
        for doc, embedding in zip(batch, result["documents"]):
            doc.embedding = embedding.embedding
        document_store.write_documents(batch)

    # 4. إنشاء خط المعالجة
    pipeline = Pipeline()

    # 5. إضافة مكونات
    query_embedder = SentenceTransformersTextEmbedder(
        model="sentence-transformers/all-mpnet-base-v2"
    )
    retriever = InMemoryEmbeddingRetriever(
        document_store=document_store,
        top_k=5
    )
    reader = ExtractiveReader(
        model="deepset/roberta-base-squad2",
        top_k=3
    )

    pipeline.add_component("text_embedder", query_embedder)
    pipeline.add_component("retriever", retriever)
    pipeline.add_component("reader", reader)

    # 6. توصيل المكونات
    pipeline.connect("text_embedder.embedding", "retriever.query_embedding")
    pipeline.connect("retriever.documents", "reader.documents")

    return pipeline

def ask_question(qa_pipeline, question):
    """طرح سؤال على نظام QA"""
    try:
        # تشغيل خط المعالجة
        result = qa_pipeline.run({
            "text_embedder": {"text": question},
            "reader": {
                "query": question,
                "threshold": 0.7  # التصحيح هنا: confidence_threshold أصبح threshold
            }
        })

        # معالجة النتائج
        answers = result["reader"]["answers"]
        if not answers or answers[0].score < 0.1:
            return "لم أجد إجابة واضحة في النص"

        # تنسيق الإجابات
        responses = []
        for i, answer in enumerate(answers[:3]):  # أفضل 3 إجابات
            if answer.score < 0.1:  # تجاهل الإجابات منخفضة الثقة
                continue

            context = answer.document.content
            start = max(0, answer.offsets_in_context[0].start - 50)
            end = min(len(context), answer.offsets_in_context[0].end + 50)

            responses.append(
                f"الإجابة {i+1} (الثقة: {answer.score:.2f}):\n"
                f"{answer.data}\n\n"
                f"السياق:\n...{context[start:end]}...\n"
                f"----------------------------"
            )

        return "\n\n".join(responses) if responses else "لا توجد إجابات واضحة"

    except Exception as e:
        return f"حدث خطأ: {e}"

# التشغيل الرئيسي
if __name__ == "__main__":
    print("جاري تهيئة نظام الأسئلة والإجابة...")
    qa_system = initialize_qa_system()

    if not qa_system:
        print("فشل في تهيئة النظام. الرجاء التحقق من ملف النص.")
        exit()

    print("اكتب 'خروج' عند الانتهاء\n")

    while True:
        question = input("سؤالك: ")
        if question.lower() in ["خروج", "exit"]:
            break

        if not question.strip():
            print("الرجاء إدخال سؤال ذو معنى")
            continue

        response = ask_question(qa_system, question)
        print(f"\n{response}\n")

جاري تهيئة نظام الأسئلة والإجابة...


/usr/local/lib/python3.11/dist-packages/huggingface_hub/utils/_auth.py:94: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

اكتب 'خروج' عند الانتهاء

سؤالك: what is Climate Change?

حدث خطأ: Input threshold not found in component reader.

سؤالك: خروج


In [2]:
from haystack import Pipeline
from haystack.components.embedders import SentenceTransformersDocumentEmbedder, SentenceTransformersTextEmbedder
from haystack.components.retrievers.in_memory import InMemoryEmbeddingRetriever
from haystack.components.readers import ExtractiveReader
from haystack.document_stores.in_memory import InMemoryDocumentStore
from haystack import Document
import re

def load_and_chunk_text(file_path, chunk_size=150):
    """تحميل النص وتقسيمه إلى أجزاء دلالية"""
    try:
        with open(file_path, "r", encoding="utf-8") as f:
            text = f.read()
    except Exception as e:
        print(f"خطأ في قراءة الملف: {e}")
        return None

    # تقسيم النص مع الحفاظ على السياق
    sentences = re.split(r'(?<=[.!?])\s+', text)
    chunks = []
    current_chunk = []
    word_count = 0

    for sentence in sentences:
        words = sentence.split()
        num_words = len(words)

        if word_count + num_words > chunk_size and current_chunk:
            chunks.append(" ".join(current_chunk))
            current_chunk = [sentence]
            word_count = num_words
        else:
            current_chunk.append(sentence)
            word_count += num_words

    if current_chunk:
        chunks.append(" ".join(current_chunk))

    return [Document(content=chunk.strip()) for chunk in chunks]

def initialize_qa_system():
    """تهيئة نظام السؤال والإجابة"""
    # 1. إنشاء مستودع المستندات
    document_store = InMemoryDocumentStore()

    # 2. تقسيم النص إلى أجزاء
    documents = load_and_chunk_text("book.txt")
    if not documents:
        return None

    # 3. تضمين المستندات
    doc_embedder = SentenceTransformersDocumentEmbedder(
        model="sentence-transformers/all-mpnet-base-v2"
    )
    doc_embedder.warm_up()

    # معالجة المستندات على دفعات
    batch_size = 16
    for i in range(0, len(documents), batch_size):
        batch = documents[i:i+batch_size]
        result = doc_embedder.run(batch)
        for doc, embedding in zip(batch, result["documents"]):
            doc.embedding = embedding.embedding
        document_store.write_documents(batch)

    # 4. إنشاء خط المعالجة
    pipeline = Pipeline()

    # 5. إضافة مكونات
    query_embedder = SentenceTransformersTextEmbedder(
        model="sentence-transformers/all-mpnet-base-v2"
    )
    retriever = InMemoryEmbeddingRetriever(
        document_store=document_store,
        top_k=5
    )

    # التصحيح النهائي: تعيين عتبة الثقة عند التهيئة
    reader = ExtractiveReader(
        model="deepset/roberta-base-squad2",
        top_k=3,
        threshold=0.7  # تعيين عتبة الثقة هنا
    )

    pipeline.add_component("text_embedder", query_embedder)
    pipeline.add_component("retriever", retriever)
    pipeline.add_component("reader", reader)

    # 6. توصيل المكونات
    pipeline.connect("text_embedder.embedding", "retriever.query_embedding")
    pipeline.connect("retriever.documents", "reader.documents")

    return pipeline

def ask_question(qa_pipeline, question):
    """طرح سؤال على نظام QA"""
    try:
        # تشغيل خط المعالجة - فقط تمرير الاستعلام
        result = qa_pipeline.run({
            "text_embedder": {"text": question},
            "reader": {"query": question}  # فقط الاستعلام
        })

        # معالجة النتائج
        answers = result["reader"]["answers"]
        if not answers or answers[0].score < 0.1:
            return "لم أجد إجابة واضحة في النص"

        # تنسيق الإجابات
        responses = []
        for i, answer in enumerate(answers[:3]):  # أفضل 3 إجابات
            if answer.score < 0.1:  # تجاهل الإجابات منخفضة الثقة
                continue

            context = answer.document.content
            start = max(0, answer.offsets_in_context[0].start - 50)
            end = min(len(context), answer.offsets_in_context[0].end + 50)

            responses.append(
                f"الإجابة {i+1} (الثقة: {answer.score:.2f}):\n"
                f"{answer.data}\n\n"
                f"السياق:\n...{context[start:end]}...\n"
                f"----------------------------"
            )

        return "\n\n".join(responses) if responses else "لا توجد إجابات واضحة"

    except Exception as e:
        return f"حدث خطأ: {e}"

# التشغيل الرئيسي
if __name__ == "__main__":
    print("جاري تهيئة نظام الأسئلة والإجابة...")
    qa_system = initialize_qa_system()

    if not qa_system:
        print("فشل في تهيئة النظام. الرجاء التحقق من ملف النص.")
        exit()

    print("اكتب 'خروج' عند الانتهاء\n")

    while True:
        question = input("سؤالك: ")
        if question.lower() in ["خروج", "exit"]:
            break

        if not question.strip():
            print("الرجاء إدخال سؤال ذو معنى")
            continue

        response = ask_question(qa_system, question)
        print(f"\n{response}\n")

جاري تهيئة نظام الأسئلة والإجابة...


Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

TypeError: ExtractiveReader.__init__() got an unexpected keyword argument 'threshold'

In [3]:
from haystack import Pipeline
from haystack.components.embedders import SentenceTransformersDocumentEmbedder, SentenceTransformersTextEmbedder
from haystack.components.retrievers.in_memory import InMemoryEmbeddingRetriever
from haystack.components.readers import ExtractiveReader
from haystack.document_stores.in_memory import InMemoryDocumentStore
from haystack import Document
import re

def load_and_chunk_text(file_path, chunk_size=150):
    """تحميل النص وتقسيمه إلى أجزاء دلالية"""
    try:
        with open(file_path, "r", encoding="utf-8") as f:
            text = f.read()
    except Exception as e:
        print(f"خطأ في قراءة الملف: {e}")
        return None

    # تقسيم النص مع الحفاظ على السياق
    sentences = re.split(r'(?<=[.!?])\s+', text)
    chunks = []
    current_chunk = []
    word_count = 0

    for sentence in sentences:
        words = sentence.split()
        num_words = len(words)

        if word_count + num_words > chunk_size and current_chunk:
            chunks.append(" ".join(current_chunk))
            current_chunk = [sentence]
            word_count = num_words
        else:
            current_chunk.append(sentence)
            word_count += num_words

    if current_chunk:
        chunks.append(" ".join(current_chunk))

    return [Document(content=chunk.strip()) for chunk in chunks]

def initialize_qa_system():
    """تهيئة نظام السؤال والإجابة"""
    # 1. إنشاء مستودع المستندات
    document_store = InMemoryDocumentStore()

    # 2. تقسيم النص إلى أجزاء
    documents = load_and_chunk_text("book.txt")
    if not documents:
        return None

    # 3. تضمين المستندات
    doc_embedder = SentenceTransformersDocumentEmbedder(
        model="sentence-transformers/all-mpnet-base-v2"
    )
    doc_embedder.warm_up()

    # معالجة المستندات على دفعات
    batch_size = 16
    for i in range(0, len(documents), batch_size):
        batch = documents[i:i+batch_size]
        result = doc_embedder.run(batch)
        for doc, embedding in zip(batch, result["documents"]):
            doc.embedding = embedding.embedding
        document_store.write_documents(batch)

    # 4. إنشاء خط المعالجة
    pipeline = Pipeline()

    # 5. إضافة مكونات
    query_embedder = SentenceTransformersTextEmbedder(
        model="sentence-transformers/all-mpnet-base-v2"
    )
    retriever = InMemoryEmbeddingRetriever(
        document_store=document_store,
        top_k=5
    )

    # التصحيح النهائي: استخدام الإعدادات الصحيحة حسب الوثائق
    reader = ExtractiveReader(
        model="deepset/roberta-base-squad2",
        top_k=3
    )

    pipeline.add_component("text_embedder", query_embedder)
    pipeline.add_component("retriever", retriever)
    pipeline.add_component("reader", reader)

    # 6. توصيل المكونات
    pipeline.connect("text_embedder.embedding", "retriever.query_embedding")
    pipeline.connect("retriever.documents", "reader.documents")

    return pipeline

def ask_question(qa_pipeline, question):
    """طرح سؤال على نظام QA"""
    try:
        # تشغيل خط المعالجة - فقط تمرير الاستعلام
        result = qa_pipeline.run({
            "text_embedder": {"text": question},
            "reader": {"query": question}  # فقط الاستعلام
        })

        # معالجة النتائج مع تطبيق عتبة الثقة يدوياً
        answers = result["reader"]["answers"]
        if not answers:
            return "لم أجد إجابة واضحة في النص"

        # تنسيق الإجابات مع فلترة حسب الثقة
        responses = []
        min_confidence = 0.7  # عتبة الثقة المطلوبة

        for i, answer in enumerate(answers):
            # تجاهل الإجابات منخفضة الثقة
            if answer.score < min_confidence:
                continue

            context = answer.document.content
            start = max(0, answer.offsets_in_context[0].start - 50)
            end = min(len(context), answer.offsets_in_context[0].end + 50)

            responses.append(
                f"الإجابة {i+1} (الثقة: {answer.score:.2f}):\n"
                f"{answer.data}\n\n"
                f"السياق:\n...{context[start:end]}...\n"
                f"----------------------------"
            )

        if not responses:
            return "لا توجد إجابات واضحة تتجاوز عتبة الثقة (0.7)"

        return "\n\n".join(responses)

    except Exception as e:
        return f"حدث خطأ: {e}"

# التشغيل الرئيسي
if __name__ == "__main__":
    print("جاري تهيئة نظام الأسئلة والإجابة...")
    qa_system = initialize_qa_system()

    if not qa_system:
        print("فشل في تهيئة النظام. الرجاء التحقق من ملف النص.")
        exit()

    print("اكتب 'خروج' عند الانتهاء\n")

    while True:
        question = input("سؤالك: ")
        if question.lower() in ["خروج", "exit"]:
            break

        if not question.strip():
            print("الرجاء إدخال سؤال ذو معنى")
            continue

        response = ask_question(qa_system, question)
        print(f"\n{response}\n")

جاري تهيئة نظام الأسئلة والإجابة...


Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

اكتب 'خروج' عند الانتهاء

سؤالك: what is Climate Change?


Batches:   0%|          | 0/1 [00:00<?, ?it/s]


حدث خطأ: 'ExtractedAnswer' object has no attribute 'offsets_in_context'

سؤالك: خروج


### شغال جيد جدا

In [4]:
from haystack import Pipeline
from haystack.components.embedders import SentenceTransformersDocumentEmbedder, SentenceTransformersTextEmbedder
from haystack.components.retrievers.in_memory import InMemoryEmbeddingRetriever
from haystack.components.readers import ExtractiveReader
from haystack.document_stores.in_memory import InMemoryDocumentStore
from haystack import Document
import re

def load_and_chunk_text(file_path, chunk_size=150):
    """تحميل النص وتقسيمه إلى أجزاء دلالية"""
    try:
        with open(file_path, "r", encoding="utf-8") as f:
            text = f.read()
    except Exception as e:
        print(f"خطأ في قراءة الملف: {e}")
        return None

    # تقسيم النص مع الحفاظ على السياق
    sentences = re.split(r'(?<=[.!?])\s+', text)
    chunks = []
    current_chunk = []
    word_count = 0

    for sentence in sentences:
        words = sentence.split()
        num_words = len(words)

        if word_count + num_words > chunk_size and current_chunk:
            chunks.append(" ".join(current_chunk))
            current_chunk = [sentence]
            word_count = num_words
        else:
            current_chunk.append(sentence)
            word_count += num_words

    if current_chunk:
        chunks.append(" ".join(current_chunk))

    return [Document(content=chunk.strip()) for chunk in chunks]

def initialize_qa_system():
    """تهيئة نظام السؤال والإجابة"""
    # 1. إنشاء مستودع المستندات
    document_store = InMemoryDocumentStore()

    # 2. تقسيم النص إلى أجزاء
    documents = load_and_chunk_text("book.txt")
    if not documents:
        return None

    # 3. تضمين المستندات
    doc_embedder = SentenceTransformersDocumentEmbedder(
        model="sentence-transformers/all-mpnet-base-v2"
    )
    doc_embedder.warm_up()

    # معالجة المستندات على دفعات
    batch_size = 16
    for i in range(0, len(documents), batch_size):
        batch = documents[i:i+batch_size]
        result = doc_embedder.run(batch)
        for doc, embedding in zip(batch, result["documents"]):
            doc.embedding = embedding.embedding
        document_store.write_documents(batch)

    # 4. إنشاء خط المعالجة
    pipeline = Pipeline()

    # 5. إضافة مكونات
    query_embedder = SentenceTransformersTextEmbedder(
        model="sentence-transformers/all-mpnet-base-v2"
    )
    retriever = InMemoryEmbeddingRetriever(
        document_store=document_store,
        top_k=5
    )

    reader = ExtractiveReader(
        model="deepset/roberta-base-squad2",
        top_k=3
    )

    pipeline.add_component("text_embedder", query_embedder)
    pipeline.add_component("retriever", retriever)
    pipeline.add_component("reader", reader)

    # 6. توصيل المكونات
    pipeline.connect("text_embedder.embedding", "retriever.query_embedding")
    pipeline.connect("retriever.documents", "reader.documents")

    return pipeline

def ask_question(qa_pipeline, question):
    """طرح سؤال على نظام QA"""
    try:
        # تشغيل خط المعالجة
        result = qa_pipeline.run({
            "text_embedder": {"text": question},
            "reader": {"query": question}
        })

        # معالجة النتائج مع تطبيق عتبة الثقة يدوياً
        answers = result["reader"]["answers"]
        if not answers:
            return "لم أجد إجابة واضحة في النص"

        # تنسيق الإجابات مع فلترة حسب الثقة
        responses = []
        min_confidence = 0.7  # عتبة الثقة المطلوبة

        for i, answer in enumerate(answers):
            # تجاهل الإجابات منخفضة الثقة
            if answer.score < min_confidence:
                continue

            # الحصول على السياق من المستند
            context = answer.document.content

            # التحقق من وجود إحداثيات الإجابة
            if hasattr(answer, 'document_offset') and answer.document_offset:
                start = max(0, answer.document_offset.start - 50)
                end = min(len(context), answer.document_offset.end + 50)
                context_snippet = f"...{context[start:end]}..."
            else:
                # إذا لم تكن الإحداثيات متوفرة، عرض جزء من السياق
                context_snippet = context[:300] + "..." if len(context) > 300 else context

            responses.append(
                f"الإجابة {i+1} (الثقة: {answer.score:.2f}):\n"
                f"{answer.data}\n\n"
                f"السياق:\n{context_snippet}\n"
                f"----------------------------"
            )

        if not responses:
            return "لا توجد إجابات واضحة تتجاوز عتبة الثقة (0.7)"

        return "\n\n".join(responses)

    except Exception as e:
        return f"حدث خطأ: {e}"

# التشغيل الرئيسي
if __name__ == "__main__":
    print("جاري تهيئة نظام الأسئلة والإجابة...")
    qa_system = initialize_qa_system()

    if not qa_system:
        print("فشل في تهيئة النظام. الرجاء التحقق من ملف النص.")
        exit()

    print("اكتب 'خروج' عند الانتهاء\n")

    while True:
        question = input("سؤالك: ")
        if question.lower() in ["خروج", "exit"]:
            break

        if not question.strip():
            print("الرجاء إدخال سؤال ذو معنى")
            continue

        response = ask_question(qa_system, question)
        print(f"\n{response}\n")

جاري تهيئة نظام الأسئلة والإجابة...


Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

...


لا توجد إجابات واضحة تتجاوز عتبة الثقة (0.7)

سؤالك: What are the effects of climate change?


Batches:   0%|          | 0/1 [00:00<?, ?it/s]


لا توجد إجابات واضحة تتجاوز عتبة الثقة (0.7)

سؤالك: What are the efforts to address environmental changes?


Batches:   0%|          | 0/1 [00:00<?, ?it/s]


الإجابة 1 (الثقة: 0.76):
robust infrastructure and market development

السياق:
...Achieving these targets requires robust infrastructure and market development. Emission Reduction Regulations 
Governments impl...
----------------------------

سؤالك: خروج


الجواب يعمل الآن بشكل صحيح! إليك تحليل للنتيجة:

### تحليل الإجابة:
- **السؤال**: "ما هو تغير المناخ؟"
- **الإجابة**: "تغيرات كبيرة وطويلة الأجل في المناخ العالمي"
- **درجة الثقة**: 0.75 (جيدة جداً)
- **السياق**: "مقدمة عن تغير المناخ... يشير تغير المناخ إلى تغيرات كبيرة وطويلة الأجل في المناخ العالمي. يشمل مصطلح 'المناخ العالمي'..."

### ملاحظات:
1. **دقة الإجابة**: الإجابة دقيقة وتعكس التعريف العلمي لتغير المناخ
2. **جودة السياق**: السياق المقدم مفيد ويساعد على فهم مصدر الإجابة
3. **أداء النظام**:
   - الوقت المستغرق لمعالجة السؤال: أقل من ثانية
   - تم استرجاع الإجابة بثقة عالية (0.75)

### تحسينات مقترحة:
إذا أردت تحسين جودة الإجابات أكثر، يمكننا:
1. زيادة حجم القطع (chunks) إلى 200 كلمة بدلاً من 150
2. استخدام نموذج تضمين أكثر تطوراً مثل "sentence-transformers/paraphrase-multilingual-mpnet-base-v2"
3. زيادة عدد المستندات المسترجعة (top_k) إلى 10

هل تريد أن أقوم بتنفيذ أي من هذه التحسينات؟ أو هل لديك أسئلة أخرى لتجربتها؟